# Data Science Internship at Data Glacier

Name: Harshith Sakala Santhosh

Group-Name: Gold Standard Team,LISUM-19

Email-id: sakala.harshith@gmail.com

Country: United Kingdom

Team Members:

1) Harshith Sakala Santhosh

2) Mario Rodriques Peres

3) Alexis Michael-Igbokwe


## Final Project: Predicting the persistency of a drug (Healthcare) - Part 4

#### Problem Description

One of the challenge for all Pharmaceutical companies is to understand the persistency of drug as per the physician prescription. To solve this problem ABC pharma company approached an analytics company to automate this process of identification.

With an objective to gather insights on the factors that are impacting the persistency, a classification
model will be built for the given dataset.

***1. Loading the packages and dataset***

In [1]:
!pip install pandas-profiling

In [2]:
# Loading package
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
#from ydata_profiling import ProfileReport
import pandas_profiling
from scipy.stats import chi2_contingency, pointbiserialr, f_oneway, pearsonr, ttest_ind
from statsmodels.stats.weightstats import ztest
from sklearn.preprocessing import LabelEncoder

C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\3049380075.py:7: DeprecationWarning: `import pandas_profiling` is going to be deprecated by April 1st. Please use `import ydata_profiling` instead.
  import pandas_profiling


In [3]:
# Loading the dataset
df = pd.read_excel("Healthcare_dataset.xlsx", sheet_name="Dataset")

***2. Creating an statistical summary***

In [4]:
# Profile Report

# There are no null and duplicate values present in the data
list_duplicated_values_boolean=df.duplicated()
print("This actually is an indicator of Duplicated rows if present it is going to return true or else false:",True in list_duplicated_values_boolean)
pandas_profiling.ProfileReport(df)

This actually is an indicator of Duplicated rows if present it is going to return true or else false: False


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### Approach 1

***3. Treating outliers***

In [5]:
# Creating a new dataframe for the approach 1
df1 = df.copy()

* Dexa_Freq_During_Rx

In [6]:
# Ploting the boxplot for Dexa_Freq_During_Rx
q1,q2=np.percentile(df1['Dexa_Freq_During_Rx'],[25,75])
print(q1,q2)
IQR=q2-q1
print("The inter quartile range of the dexa_freq_During_Rx entire data regardless of output label is :{inter}".format(inter=IQR))
lower_bound=q1-(1.5*IQR)
upper_bound=q2+(1.5*IQR)
print("The lower bound of the dexa_freq_During_Rx entire data regardless of output label is :{lower}".format(lower=lower_bound),"The uppper bound of the dexa_freq_During_Rx data is :{upper}".format(upper=upper_bound))
sns.boxplot(x=df1['Dexa_Freq_During_Rx'])

0.0 3.0
The inter quartile range of the dexa_freq_During_Rx entire data regardless of output label is :3.0
The lower bound of the dexa_freq_During_Rx entire data regardless of output label is :-4.5 The uppper bound of the dexa_freq_During_Rx data is :7.5


<Axes: xlabel='Dexa_Freq_During_Rx'>

In [7]:
#Plot the Dexa freq values where persistencyflag==Persistent
number_of_persistent_values_in_Dexa=df1[df1['Persistency_Flag']=='Persistent']
q1,median,q2= np.percentile(number_of_persistent_values_in_Dexa['Dexa_Freq_During_Rx'],[25,50,75])

IQR_Persistent=q2-q1
print("The Inter Quartile Range of  dexa frequency values for persistency is {Pers}".format(Pers=IQR))
lower_bound_pers=q1-(1.5*IQR_Persistent)
upper_bound_pers=q2+(1.5*IQR_Persistent)
print("The lower bound of the dexa_freq_During_Rx entire data regardless of output label is :{lower}".format(lower=lower_bound_pers))
print("The upper bound of the dexa_freq_During_Rx data is :{upper}".format(upper=upper_bound_pers))
sns.boxplot(x=number_of_persistent_values_in_Dexa['Dexa_Freq_During_Rx'])


The Inter Quartile Range of  dexa frequency values for persistency is 3.0
The lower bound of the dexa_freq_During_Rx entire data regardless of output label is :-13.5
The upper bound of the dexa_freq_During_Rx data is :22.5


<Axes: xlabel='Dexa_Freq_During_Rx'>

In [8]:
#Plot the Dexa freq values where persistencyflag==Non-Persistent
number_of_non_persistent_values_in_Dexa=df1[df1['Persistency_Flag']=='Non-Persistent']
q1,q2= np.percentile(number_of_non_persistent_values_in_Dexa['Dexa_Freq_During_Rx'],[25,75])
IQR_Non_Persistent=q2-q1
print("The Inter Quartile Range of  dexa frequency values for persistency is {Pers}".format(Pers=IQR))
lower_bound_Non_pers=q1-(1.5*IQR_Non_Persistent)
upper_bound_Non_pers=q2+(1.5*IQR_Non_Persistent)
print("The lower bound of the dexa_freq_During_Rx entire data regardless of output label is :{lower}".format(lower=lower_bound_Non_pers))
print("The upper bound of the dexa_freq_During_Rx data is :{upper}".format(upper=upper_bound_Non_pers))
sns.boxplot(x=number_of_non_persistent_values_in_Dexa['Dexa_Freq_During_Rx'])

# Since it is clear that there are outliers present in both values and there is variance observed between the distribution of these two value distributions.
# The outlier values for both Persistent and Non_persistent will be replace by taking the median values of respected distributions and also the median value for Non_persistent data is 0.


The Inter Quartile Range of  dexa frequency values for persistency is 3.0
The lower bound of the dexa_freq_During_Rx entire data regardless of output label is :0.0
The upper bound of the dexa_freq_During_Rx data is :0.0


<Axes: xlabel='Dexa_Freq_During_Rx'>

In [9]:
# Dealing with outliers by replacing the outlier values by median of both persistent and non persistent dexa freq values
persistent_data=df1[df1['Persistency_Flag']=='Persistent']
median_value=persistent_data['Dexa_Freq_During_Rx'].median()
df1['Dexa_Freq_During_Rx'] = np.where((df1['Persistency_Flag'] == 'Persistent') & (df1['Dexa_Freq_During_Rx']>22.5),median_value , df1['Dexa_Freq_During_Rx'])
df1['Dexa_Freq_During_Rx'] = np.where((df1['Persistency_Flag'] == 'Non-Persistent') & (df1['Dexa_Freq_During_Rx']>0),0 , df1['Dexa_Freq_During_Rx'])
print("The minimum value of Dexa_Freq_During_Rx is {min}".format(min=df1['Dexa_Freq_During_Rx'].min()))
print("The maximum value of Dexa_Freq_During_Rx is {max}".format(max=df1['Dexa_Freq_During_Rx'].max()))
persistent1_data=df1[df1['Persistency_Flag']=='Persistent']
non_persistent_data=df1[df1['Persistency_Flag']=='Non-Persistent']
print(non_persistent_data[['Dexa_Freq_During_Rx','Persistency_Flag']].max())
#Dexa freq values for persistent
sns.boxplot(x=persistent1_data['Dexa_Freq_During_Rx'])

The minimum value of Dexa_Freq_During_Rx is 0.0
The maximum value of Dexa_Freq_During_Rx is 22.0
Dexa_Freq_During_Rx               0.0
Persistency_Flag       Non-Persistent
dtype: object


<Axes: xlabel='Dexa_Freq_During_Rx'>

In [10]:
#Dexa freq values for non-persistent
sns.boxplot(x=non_persistent_data['Dexa_Freq_During_Rx'])


<Axes: xlabel='Dexa_Freq_During_Rx'>




*   Count_Of_Risks






In [11]:
#Plot count of risks for persistent values
number_of_persistent_values_in_count_of_risks=df1[df1['Persistency_Flag']=='Persistent']
q1,median,q2= np.percentile(number_of_persistent_values_in_Dexa['Count_Of_Risks'],[25,50,75])

IQR_Persistent=q2-q1
print("The Inter Quartile Range of  count of risks for persistency is {Pers}".format(Pers=IQR))
lower_bound_pers=q1-(1.5*IQR_Persistent)
upper_bound_pers=q2+(1.5*IQR_Persistent)
print("The lower bound of the count of risks is :{lower}".format(lower=lower_bound_pers))
print("The upper bound of the count of risks data is :{upper}".format(upper=upper_bound_pers))
sns.boxplot(x=number_of_persistent_values_in_Dexa['Count_Of_Risks'])

The Inter Quartile Range of  count of risks for persistency is 3.0
The lower bound of the count of risks is :-0.5
The upper bound of the count of risks data is :3.5


<Axes: xlabel='Count_Of_Risks'>

In [12]:
#Plot count of risks for non-persistent values
number_of_non_persistent_values_in_count_of_risks=df1[df1['Persistency_Flag']=='Non-Persistent']
q1,q2= np.percentile(number_of_non_persistent_values_in_count_of_risks['Count_Of_Risks'],[25,75])
IQR_Non_Persistent=q2-q1
print("The Inter Quartile Range of  count of risks values for persistency is {Pers}".format(Pers=IQR))
lower_bound_Non_pers=q1-(1.5*IQR_Non_Persistent)
upper_bound_Non_pers=q2+(1.5*IQR_Non_Persistent)
print("The lower bound of the count of risksis :{lower}".format(lower=lower_bound_Non_pers))
print("The upper bound of the count of risks data is :{upper}".format(upper=upper_bound_Non_pers))
sns.boxplot(x=number_of_non_persistent_values_in_Dexa['Count_Of_Risks'])


The Inter Quartile Range of  count of risks values for persistency is 3.0
The lower bound of the count of risksis :-3.0
The upper bound of the count of risks data is :5.0


<Axes: xlabel='Count_Of_Risks'>

In [13]:
# Similar to previous feature, replacing all outliers with median values of both persistent values
persistent_data=df1[df1['Persistency_Flag']=='Persistent']
median_value=persistent_data['Count_Of_Risks'].median()
persistent_data=df1[df1['Persistency_Flag']=='Non-Persistent']
non_persistency_median_value=persistent_data['Count_Of_Risks'].median()
df1['Count_Of_Risks'] = np.where((df1['Persistency_Flag'] == 'Persistent') & (df1['Count_Of_Risks']>3.5),median_value , df1['Count_Of_Risks'])
df1['Count_Of_Risks'] = np.where((df1['Persistency_Flag'] == 'Non-Persistent') & (df1['Count_Of_Risks']>5),non_persistency_median_value, df1['Count_Of_Risks'])
print("The minimum value of Count_Of_Risks is {min}".format(min=df1['Dexa_Freq_During_Rx'].min()))
print("The maximum value of Count_Of_Risks is {max}".format(max=df1['Dexa_Freq_During_Rx'].max()))
persistent1_data=df1[df1['Persistency_Flag']=='Persistent']
non_persistent_data=df1[df1['Persistency_Flag']=='Non-Persistent']
print(non_persistent_data[['Count_Of_Risks','Persistency_Flag']].max())
sns.boxplot(x=persistent1_data['Count_Of_Risks'])




The minimum value of Count_Of_Risks is 0.0
The maximum value of Count_Of_Risks is 22.0
Count_Of_Risks                 5.0
Persistency_Flag    Non-Persistent
dtype: object


<Axes: xlabel='Count_Of_Risks'>

In [14]:
#Boxplot of Count of Risks for Non-persistent values
sns.boxplot(x=non_persistent_data['Count_Of_Risks'])

<Axes: xlabel='Count_Of_Risks'>

***4. Encoding categorical variables***

In [15]:
# Creating a dataframe with only the numerical variables
numerical_data_frame=df1[['Dexa_Freq_During_Rx','Count_Of_Risks']]

# Removing the numerical variables from df1
df1.drop(['Dexa_Freq_During_Rx','Count_Of_Risks'],axis=1,inplace=True)

# Applying the label encoding
df1=df1.apply(LabelEncoder().fit_transform)

***5. Creating the transformed dataset and visualizing it***

In [16]:
# Joining the numerical and categorical variables badk in df1
df1 = pd.concat([pd.DataFrame(df1), pd.DataFrame(numerical_data_frame, columns=['Dexa_Freq_During_Rx','Count_Of_Risks'])], axis=1)

# Visualizing the number of registers
print('There are {} registers in df1'.format(len(df1)))

# Vizualizing the new dataframe after transformation
df1.head()

There are 3424 registers in df1


Ptid  Persistency_Flag  Gender  Race  Ethnicity  Region  Age_Bucket  \
0     0                 1       1     2          1       4           3   
1  1111                 0       1     1          1       4           0   
2  2222                 0       0     3          0       0           1   
3  2758                 0       0     2          1       0           3   
4  2869                 0       0     2          1       0           3   

   Ntm_Speciality  Ntm_Specialist_Flag  Ntm_Speciality_Bucket  ...  \
0               5                    0                      1  ...   
1               5                    0                      1  ...   
2               5                    0                      1  ...   
3               5                    0                      1  ...   
4               5                    0                      1  ...   

   Risk_Low_Calcium_Intake  Risk_Vitamin_D_Insufficiency  \
0                        0                             0   
1                        0                             0   
2                        1                             0   
3                        0                             0   
4                        0                             0   

   Risk_Poor_Health_Frailty  Risk_Excessive_Thinness  \
0                         0                        0   
1                         0                        0   
2                         0                        0   
3                         0                        0   
4                         0                        0   

   Risk_Hysterectomy_Oophorectomy  Risk_Estrogen_Deficiency  \
0                               0                         0   
1                               0                         0   
2                               0                         0   
3                               0                         0   
4                               0                         0   

   Risk_Immobilization  Risk_Recurring_Falls  Dexa_Freq_During_Rx  \
0                    0                     0                  0.0   
1                    0                     0                  0.0   
2                    0                     0                  0.0   
3                    0                     0                  0.0   
4                    0                     0                  0.0   

   Count_Of_Risks  
0             0.0  
1             0.0  
2             2.0  
3             1.0  
4             1.0  

[5 rows x 69 columns]

### Approach 2

***3. Treating outliers***

In [17]:
# Creating a new dataframe to hold all the categorical and boolean variables, including the target
# variable.
df_obj = df.select_dtypes(include='object')

# Creating a new dataframe to hold all the numeric variables
df_num = df.drop(columns=df_obj.columns)

# Copying the variable Persistency_Flag into the df_num
df_num['Persistency_Flag'] = df['Persistency_Flag']

* Dexa_Freq_During_Rx

In [18]:
# Ploting the boxplot for the 'Dexa_Freq_During_Rx' considering the target variables
df_num[['Persistency_Flag', 'Dexa_Freq_During_Rx']].groupby('Persistency_Flag').plot(kind='box')

Persistency_Flag
Non-Persistent    Axes(0.125,0.11;0.775x0.77)
Persistent        Axes(0.125,0.11;0.775x0.77)
dtype: object

In [19]:
# Calculating the outlier threashold for the 'Dexa_Freq_During_Rx' considering the Persistency_Flag
quartiles = df_num[['Persistency_Flag', 'Dexa_Freq_During_Rx']].groupby('Persistency_Flag').quantile([0.25,0.75])

upperLimitOutlier0 = float(quartiles.iloc[1] + 1.5 * abs(np.subtract(quartiles.iloc[0], quartiles.iloc[1])))
upperLimitOutlier1 = float(quartiles.iloc[3] + 1.5 * abs(np.subtract(quartiles.iloc[2], quartiles.iloc[3])))

print(upperLimitOutlier0)
print(upperLimitOutlier1)

0.0
22.5


In [20]:
# Creating a new variable 'Dexa_Freq_During_Rx_TreatedOutlier'. This variable includes the transformation of
# outliers to the max value of the boxplot that is not outlier (tip of the upper tail). In this case, if the
# 'Dexa_Freq_During_RX' was higher than 0 or 22.5 for non-persistent and persistent cases, these were changed
# to these respective values (which are the upper limit values for the outliers)
Dexa_Freq_During_Rx_list = []
for i in range(len(df_num)):
    if df_num['Persistency_Flag'].iloc[i] == 'Non-Persistent':
        if df_num['Dexa_Freq_During_Rx'].iloc[i] > 0:
            Dexa_Freq_During_Rx_list.append(upperLimitOutlier0)
        else:
            Dexa_Freq_During_Rx_list.append(df_num['Dexa_Freq_During_Rx'].iloc[i])
    elif df_num['Persistency_Flag'].iloc[i] == 'Persistent':
        if df_num['Dexa_Freq_During_Rx'].iloc[i] > 22.5:
            Dexa_Freq_During_Rx_list.append(upperLimitOutlier1)
        else:
            Dexa_Freq_During_Rx_list.append(df_num['Dexa_Freq_During_Rx'].iloc[i])

df_num['Dexa_Freq_During_Rx'] = Dexa_Freq_During_Rx_list

* Count_Of_Risks

In [21]:
# Ploting the boxplot for the 'Count_Of_Risks' considering the target variables
df_num[['Persistency_Flag', 'Count_Of_Risks']].groupby('Persistency_Flag').plot(kind='box')

Persistency_Flag
Non-Persistent    Axes(0.125,0.11;0.775x0.77)
Persistent        Axes(0.125,0.11;0.775x0.77)
dtype: object

In [22]:
# Calculating the outlier threashold for the 'Count_Of_Risks' considering the Persistency_Flag
quartiles = df_num[['Persistency_Flag', 'Count_Of_Risks']].groupby('Persistency_Flag').quantile([0.25,0.75])

upperLimitOutlier0 = float(quartiles.iloc[1] + 1.5 * abs(np.subtract(quartiles.iloc[0], quartiles.iloc[1])))
upperLimitOutlier1 = float(quartiles.iloc[3] + 1.5 * abs(np.subtract(quartiles.iloc[2], quartiles.iloc[3])))

print(upperLimitOutlier0)
print(upperLimitOutlier1)

5.0
3.5


In [23]:
# Creating a new variable 'Count_Of_Risks_TreatedOutlier'. This variable includes the transformation of
# outliers to the max value of the boxplot that is not outlier (tip of the upper tail) as all outliers were
# higher values too. In this case, if the 'Count_Of_Risks' was higher than 5 or 3.5 for non-persistent and
# persistent cases, these were changed to these respective values (which are the upper limit values for the
# outliers)
Count_Of_Risks_list = []
for i in range(len(df_num)):
    if df_num['Persistency_Flag'].iloc[i] == 'Non-Persistent':
        if df_num['Count_Of_Risks'].iloc[i] > 5:
            Count_Of_Risks_list.append(upperLimitOutlier0)
        else:
            Count_Of_Risks_list.append(df_num['Count_Of_Risks'].iloc[i])
    elif df_num['Persistency_Flag'].iloc[i] == 'Persistent':
        if df_num['Count_Of_Risks'].iloc[i] > 3.5:
            Count_Of_Risks_list.append(upperLimitOutlier1)
        else:
            Count_Of_Risks_list.append(df_num['Count_Of_Risks'].iloc[i])

df_num['Count_Of_Risks'] = Count_Of_Risks_list

In [24]:
# Removing the variables before transformation and the target
df_num.drop(columns=['Persistency_Flag'], inplace=True)

***4. Encoding categorical variables***

In [25]:
# Encoding the categorical variables
for col in df_obj.columns:
    df_obj[col] = LabelEncoder().fit_transform(df_obj[col])

***5. Creating the transformed dataset and visualizing it***

In [26]:
# Creating a new dataframe to hold all the transformed variables
df2 = pd.concat([pd.DataFrame(df_obj), pd.DataFrame(df_num)], axis=1)

# Visualizing the number of registers
print('There are {} registers in df2'.format(len(df2)))

# Vizualizing the new dataframe after transformation
df2.head()

There are 3424 registers in df2


Ptid  Persistency_Flag  Gender  Race  Ethnicity  Region  Age_Bucket  \
0     0                 1       1     2          1       4           3   
1  1111                 0       1     1          1       4           0   
2  2222                 0       0     3          0       0           1   
3  2758                 0       0     2          1       0           3   
4  2869                 0       0     2          1       0           3   

   Ntm_Speciality  Ntm_Specialist_Flag  Ntm_Speciality_Bucket  ...  \
0               5                    0                      1  ...   
1               5                    0                      1  ...   
2               5                    0                      1  ...   
3               5                    0                      1  ...   
4               5                    0                      1  ...   

   Risk_Low_Calcium_Intake  Risk_Vitamin_D_Insufficiency  \
0                        0                             0   
1                        0                             0   
2                        1                             0   
3                        0                             0   
4                        0                             0   

   Risk_Poor_Health_Frailty  Risk_Excessive_Thinness  \
0                         0                        0   
1                         0                        0   
2                         0                        0   
3                         0                        0   
4                         0                        0   

   Risk_Hysterectomy_Oophorectomy  Risk_Estrogen_Deficiency  \
0                               0                         0   
1                               0                         0   
2                               0                         0   
3                               0                         0   
4                               0                         0   

   Risk_Immobilization  Risk_Recurring_Falls  Dexa_Freq_During_Rx  \
0                    0                     0                  0.0   
1                    0                     0                  0.0   
2                    0                     0                  0.0   
3                    0                     0                  0.0   
4                    0                     0                  0.0   

   Count_Of_Risks  
0             0.0  
1             0.0  
2             2.0  
3             1.0  
4             1.0  

[5 rows x 69 columns]

### Approach 3

***3. Treating outliers***

In [27]:
# Creating a new dataframe for the approach 3
df3 = df.copy()

Identifying and removing outliers

In [28]:
# Plot histogram to check distribution of column
plt.hist(df3.Count_Of_Risks, bins=7, width=0.8)
plt.xlabel('Count_Of_Risks')
plt.ylabel('Count')
plt.show()

C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2459847638.py:5: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [29]:
# Checking for descriptive statistics
df3.Count_Of_Risks.describe()

count    3424.000000
mean        1.239486
std         1.094914
min         0.000000
25%         0.000000
50%         1.000000
75%         2.000000
max         7.000000
Name: Count_Of_Risks, dtype: float64

In [30]:
upper_limit = df3.Count_Of_Risks.mean() + 3*df3.Count_Of_Risks.std()
upper_limit

4.52422941524692

In [31]:
lower_limit = df3.Count_Of_Risks.mean() - 3*df3.Count_Of_Risks.std()
lower_limit

-2.0452574526300977

In [32]:
df3 = df3[df3['Count_Of_Risks'] <= upper_limit]
df3 = df3[df3['Count_Of_Risks'] >= lower_limit]

Outlier in Dexa Frequency during RX

In [33]:
# Plot histogram to check distribution of column
plt.hist(df3.Dexa_Freq_During_Rx, bins=10, width=5.0)
plt.xlabel('Dexa_Freq_During_Rx')
plt.ylabel('Count')
plt.show()

C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\522060368.py:5: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [34]:
df3.Dexa_Freq_During_Rx.describe()

count    3401.000000
mean        3.020876
std         8.159216
min         0.000000
25%         0.000000
50%         0.000000
75%         3.000000
max       146.000000
Name: Dexa_Freq_During_Rx, dtype: float64

In [35]:
upper_limit1 = df3.Dexa_Freq_During_Rx.mean() + 3*df3.Dexa_Freq_During_Rx.std()
upper_limit1

27.498523039056078

In [36]:
lower_limit1 = df3.Dexa_Freq_During_Rx.mean() - 3*df3.Dexa_Freq_During_Rx.std()
lower_limit1

-21.456770613298946

In [37]:
df3 = df3[df3['Dexa_Freq_During_Rx'] <= upper_limit1]
df3 = df3[df3['Dexa_Freq_During_Rx'] >= lower_limit1]

***4. Encoding categorical variables***

In [38]:
# Creating a new dataframe to hold all the categorical and boolean variables, including the target
# variable.
df_obj = df3.select_dtypes(include='object')

# Creating a new dataframe to hold all the numeric variables
df3 = df3.drop(columns=df_obj.columns)

# Encoding the categorical variables
for col in df_obj.columns:
    df_obj[col] = LabelEncoder().fit_transform(df_obj[col])

***5. Creating the transformed dataset and visualizing it***

In [39]:
# Creating a new dataframe to hold all the transformed variables
df3 = pd.concat([pd.DataFrame(df_obj), df3], axis=1)

# Visualizing the number of registers
print('There are {} registers in df3'.format(len(df3)))

# Vizualizing the new dataframe after transformation
df3.head()

There are 3344 registers in df3


Ptid  Persistency_Flag  Gender  Race  Ethnicity  Region  Age_Bucket  \
0     0                 1       1     2          1       4           3   
1  1093                 0       1     1          1       4           0   
2  2159                 0       0     3          0       0           1   
3  2687                 0       0     2          1       0           3   
4  2797                 0       0     2          1       0           3   

   Ntm_Speciality  Ntm_Specialist_Flag  Ntm_Speciality_Bucket  ...  \
0               5                    0                      1  ...   
1               5                    0                      1  ...   
2               5                    0                      1  ...   
3               5                    0                      1  ...   
4               5                    0                      1  ...   

   Risk_Low_Calcium_Intake  Risk_Vitamin_D_Insufficiency  \
0                        0                             0   
1                        0                             0   
2                        1                             0   
3                        0                             0   
4                        0                             0   

   Risk_Poor_Health_Frailty  Risk_Excessive_Thinness  \
0                         0                        0   
1                         0                        0   
2                         0                        0   
3                         0                        0   
4                         0                        0   

   Risk_Hysterectomy_Oophorectomy  Risk_Estrogen_Deficiency  \
0                               0                         0   
1                               0                         0   
2                               0                         0   
3                               0                         0   
4                               0                         0   

   Risk_Immobilization  Risk_Recurring_Falls  Dexa_Freq_During_Rx  \
0                    0                     0                    0   
1                    0                     0                    0   
2                    0                     0                    0   
3                    0                     0                    0   
4                    0                     0                    0   

   Count_Of_Risks  
0               0  
1               0  
2               2  
3               1  
4               1  

[5 rows x 69 columns]

## Exploratory Data Analysis

***6. Checking the Profile Report***

This report was created in the beginning of this jupyter notebook

In [40]:
# Printing the report
pandas_profiling.ProfileReport(df)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

#### Summary of Profile Report
* According to the profile report, the variable Ptid is an identification for patients, and therefore all the values are unique for this variable (high cardinality). This variable will be removed from the dataset before the modeling steps.
* The Persistency_Flag variable is the target and presents more patients from the Non-Persistent class (2135) compared to the Persistent class (1289). The dataset will have to be balanced before the modeling steps.
* The Gender variable presents much more Female registers compared to Male.
* Most of values of the variables Race and Ethnicity are from a single class (Caucasian and Not Hispanic, respectively).
* The Age_Bucket variable shows that there is an increase in the number of patients according to the increase in age.
* NTM_Speciality has high correlation with other variable(s). The correlation between Ntm_Specialist_Flag and Ntm_Speciality_Bucket with NTM_Speciality will be further investigated.
* Dexa_Freq_During_Rx presents a lot of zeros (0), which are normal values as most of patients did not have Dexa during the RX. On the other hand, this variable presents outliers, which were treated in previous steps, using three different approaches. In this case, this variable might be very correlated with the categorical variable Dexa_During_Rx. By the way, the number of N (No) for the latter variable correspond to the same number of zeros observed in the former variable.
* The variables Risk_Segment_During_Rx, Tscore_Bucket_During_Rx, Change_T_Score and Change_Risk_Segment variables present an unknown class that has to be further investigate and treated if necessary. Moreover, the higher count of values are in the unkown class for all variables.
* The Adherent_Flag, Risk_Type_1_Insulin_Dependent_Diabetes, Risk_Rheumatoid_Arthritis, Risk_Untreated_Chronic_Hypogonadism, Risk_Low_Calcium_Intake, Risk_Poor_Health_Frailty, Risk_Excessive_Thinness, Risk_Hysterectomy_Oophorectomy and Risk_Recurring_Falls variables present the great majority of values in a single class.
* Risk_Osteogenesis_Imperfecta has only 3 True values, Risk_Untreated_Chronic_Hyperthyroidism has only 2 True values, Risk_Untreated_Early_Menopause has only 12 True values, Risk_Chronic_Liver_Disease has only 18 True values, Risk_Estrogen_Deficiency has only 11 True values, and Risk_Immobilization has only 14 True values. These variables does not help with the prediction of the target and should be removed.
* The Count_Of_Risks variable presents high correlation with other variables and has to be further investigated. This variable presents a few outliers that were treated using three different approaches.

Let's use the original dataset for the exploratory analysis as we have only made changes for the two numerical variables in the approaches 1 and 2. In the end, we also make an exploratory analysis of the df3, which was the dataset transformed by removing the outliers for the numerical variables. This process may have changed the correlation between a few variables, as some registers were removed from the dataset.

***7. Checking dataset characteristics***

In [41]:
# Visualizing the shape of the dataset and the first 5 rows
print(df.shape)
df.head()

(3424, 69)


Ptid Persistency_Flag  Gender           Race     Ethnicity   Region  \
0   P1       Persistent    Male      Caucasian  Not Hispanic     West   
1   P2   Non-Persistent    Male          Asian  Not Hispanic     West   
2   P3   Non-Persistent  Female  Other/Unknown      Hispanic  Midwest   
3   P4   Non-Persistent  Female      Caucasian  Not Hispanic  Midwest   
4   P5   Non-Persistent  Female      Caucasian  Not Hispanic  Midwest   

  Age_Bucket        Ntm_Speciality Ntm_Specialist_Flag  \
0        >75  GENERAL PRACTITIONER              Others   
1      55-65  GENERAL PRACTITIONER              Others   
2      65-75  GENERAL PRACTITIONER              Others   
3        >75  GENERAL PRACTITIONER              Others   
4        >75  GENERAL PRACTITIONER              Others   

       Ntm_Speciality_Bucket  ... Risk_Family_History_Of_Osteoporosis  \
0  OB/GYN/Others/PCP/Unknown  ...                                   N   
1  OB/GYN/Others/PCP/Unknown  ...                                   N   
2  OB/GYN/Others/PCP/Unknown  ...                                   N   
3  OB/GYN/Others/PCP/Unknown  ...                                   N   
4  OB/GYN/Others/PCP/Unknown  ...                                   N   

  Risk_Low_Calcium_Intake  Risk_Vitamin_D_Insufficiency  \
0                       N                             N   
1                       N                             N   
2                       Y                             N   
3                       N                             N   
4                       N                             N   

  Risk_Poor_Health_Frailty Risk_Excessive_Thinness  \
0                        N                       N   
1                        N                       N   
2                        N                       N   
3                        N                       N   
4                        N                       N   

  Risk_Hysterectomy_Oophorectomy Risk_Estrogen_Deficiency Risk_Immobilization  \
0                              N                        N                   N   
1                              N                        N                   N   
2                              N                        N                   N   
3                              N                        N                   N   
4                              N                        N                   N   

  Risk_Recurring_Falls Count_Of_Risks  
0                    N              0  
1                    N              0  
2                    N              2  
3                    N              1  
4                    N              1  

[5 rows x 69 columns]

In [42]:
# Checking data types
df.dtypes.iloc[:40]

Ptid                                                                  object
Persistency_Flag                                                      object
Gender                                                                object
Race                                                                  object
Ethnicity                                                             object
Region                                                                object
Age_Bucket                                                            object
Ntm_Speciality                                                        object
Ntm_Specialist_Flag                                                   object
Ntm_Speciality_Bucket                                                 object
Gluco_Record_Prior_Ntm                                                object
Gluco_Record_During_Rx                                                object
Dexa_Freq_During_Rx                                                    int64

In [43]:
# Checking datatypes
df.dtypes.iloc[40:]

Concom_Narcotics                                object
Concom_Systemic_Corticosteroids_Plain           object
Concom_Anti_Depressants_And_Mood_Stabilisers    object
Concom_Fluoroquinolones                         object
Concom_Cephalosporins                           object
Concom_Macrolides_And_Similar_Types             object
Concom_Broad_Spectrum_Penicillins               object
Concom_Anaesthetics_General                     object
Concom_Viral_Vaccines                           object
Risk_Type_1_Insulin_Dependent_Diabetes          object
Risk_Osteogenesis_Imperfecta                    object
Risk_Rheumatoid_Arthritis                       object
Risk_Untreated_Chronic_Hyperthyroidism          object
Risk_Untreated_Chronic_Hypogonadism             object
Risk_Untreated_Early_Menopause                  object
Risk_Patient_Parent_Fractured_Their_Hip         object
Risk_Smoking_Tobacco                            object
Risk_Chronic_Malnutrition_Or_Malabsorption      object
Risk_Chron

In [44]:
# Checking the presence of NA values
df.isna().sum().sum()

0

***8. Categorical Variable Descriptive and Correlation Analysis***

In [45]:
# Eliminating columns that are not categorical, Persistency_Flag and Ptid
column_names=df.columns.to_list()
for x in ['Ptid','Persistency_Flag','Dexa_Freq_During_Rx','Count_Of_Risks']:
  column_names.remove(x)


In [46]:
# Calculating chisquare score between each categorical variable and Persistency_Flag
list_of_chi2_tuple=[]
for column in column_names:
  contigency= pd.crosstab(df[column], df['Persistency_Flag']) 
  plt.figure(figsize=(8,8)) 
  sns.heatmap(contigency, annot=True, cmap="YlGnBu")
  c, p, dof, expected = chi2_contingency(contigency)
  list_of_chi2_tuple.append({'name':column,'p-value':p})


C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2770713843.py:5: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`). Consider using `matplotlib.pyplot.close()`.
  plt.figure(figsize=(8,8))


In [47]:
# Plotting each categorical feature with hue Persistency_Flag

for column in column_names:
  sns.countplot(data=df,x=column,hue='Persistency_Flag')
  plt.show()
  

C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\1514821056.py:5: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()
C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\1514821056.py:5: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()
C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\1514821056.py:5: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()
C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\1514821056.py:5: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()
C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\1514821056.py:5: UserWarning: Matplotlib is currently using module://ma

In [48]:
def myFunc(e):
  return e['p-value']
list_of_chi2_tuple.sort(key=myFunc)
print("The top 15 features that are highly correlated with Persistency_Flag(Output label) as follows :")

for dictionary in list_of_chi2_tuple[0:15]:
  
  print("column_name: ",dictionary['name'],", P-value: ",dictionary['p-value']) 


The top 15 features that are highly correlated with Persistency_Flag(Output label) as follows :
column_name:  Dexa_During_Rx , P-value:  1.2280161571871475e-181
column_name:  Comorb_Long_Term_Current_Drug_Therapy , P-value:  2.725373947984128e-94
column_name:  Comorb_Encounter_For_Screening_For_Malignant_Neoplasms , P-value:  4.704163912301752e-79
column_name:  Comorb_Encounter_For_Immunization , P-value:  1.5774452734653173e-75
column_name:  Comorb_Encntr_For_General_Exam_W_O_Complaint,_Susp_Or_Reprtd_Dx , P-value:  3.0348991633791696e-64
column_name:  Comorb_Other_Disorders_Of_Bone_Density_And_Structure , P-value:  3.8439697713515143e-47
column_name:  Concom_Systemic_Corticosteroids_Plain , P-value:  1.3756487556795202e-45
column_name:  Comorb_Other_Joint_Disorder_Not_Elsewhere_Classified , P-value:  3.421072711581398e-42
column_name:  Concom_Anaesthetics_General , P-value:  2.1339524835408238e-38
column_name:  Concom_Viral_Vaccines , P-value:  2.462141024629715e-38
column_name:  Con

In [49]:
# Printing the number of unique values and categories with higher number of values (Ntm_Speciality)
print("Number of unique values: ", df['Ntm_Speciality'].nunique())
print("\n")
print("Most common classes of this variable")
df['Ntm_Speciality'].value_counts()[:5]

Number of unique values:  36


Most common classes of this variable


GENERAL PRACTITIONER    1535
RHEUMATOLOGY             604
ENDOCRINOLOGY            458
Unknown                  310
ONCOLOGY                 225
Name: Ntm_Speciality, dtype: int64

In [50]:
# Printing the number of unique values and categories with higher number of values (Risk_Osteogenesis_Imperfecta)
print("Number of unique values: ", df['Risk_Osteogenesis_Imperfecta'].nunique())
print("\n")
print("Most common classes of this variable")
df['Risk_Osteogenesis_Imperfecta'].value_counts()[:5]

Number of unique values:  2


Most common classes of this variable


N    3421
Y       3
Name: Risk_Osteogenesis_Imperfecta, dtype: int64

In [51]:
# Printing the number of unique values and categories with higher number of values (Risk_Untreated_Chronic_Hyperthyroidism)
print("Number of unique values: ", df['Risk_Untreated_Chronic_Hyperthyroidism'].nunique())
print("\n")
print("Most common classes of this variable")
df['Risk_Untreated_Chronic_Hyperthyroidism'].value_counts()[:5]

Number of unique values:  2


Most common classes of this variable


N    3422
Y       2
Name: Risk_Untreated_Chronic_Hyperthyroidism, dtype: int64

In [52]:
# Printing the number of unique values and categories with higher number of values (Risk_Untreated_Early_Menopause)
print("Number of unique values: ", df['Risk_Untreated_Early_Menopause'].nunique())
print("\n")
print("Most common classes of this variable")
df['Risk_Untreated_Early_Menopause'].value_counts()[:5]

Number of unique values:  2


Most common classes of this variable


N    3412
Y      12
Name: Risk_Untreated_Early_Menopause, dtype: int64

In [53]:
# Printing the number of unique values and categories with higher number of values (Risk_Chronic_Liver_Disease)
print("Number of unique values: ", df['Risk_Chronic_Liver_Disease'].nunique())
print("\n")
print("Most common classes of this variable")
df['Risk_Chronic_Liver_Disease'].value_counts()[:5]

Number of unique values:  2


Most common classes of this variable


N    3406
Y      18
Name: Risk_Chronic_Liver_Disease, dtype: int64

In [54]:
# Printing the number of unique values and categories with higher number of values (Risk_Low_Calcium_Intake)
print("Number of unique values: ", df['Risk_Low_Calcium_Intake'].nunique())
print("\n")
print("Most common classes of this variable")
df['Risk_Low_Calcium_Intake'].value_counts()[:5]

Number of unique values:  2


Most common classes of this variable


N    3382
Y      42
Name: Risk_Low_Calcium_Intake, dtype: int64

In [55]:
# Printing the number of unique values and categories with higher number of values (Risk_Estrogen_Deficiency)
print("Number of unique values: ", df['Risk_Estrogen_Deficiency'].nunique())
print("\n")
print("Most common classes of this variable")
df['Risk_Estrogen_Deficiency'].value_counts()[:5]

Number of unique values:  2


Most common classes of this variable


N    3413
Y      11
Name: Risk_Estrogen_Deficiency, dtype: int64

In [56]:
# Printing the number of unique values and categories with higher number of values (Risk_Immobilization)
print("Number of unique values: ", df['Risk_Immobilization'].nunique())
print("\n")
print("Most common classes of this variable")
df['Risk_Immobilization'].value_counts()[:5]

Number of unique values:  2


Most common classes of this variable


N    3410
Y      14
Name: Risk_Immobilization, dtype: int64

***Gender =>>*** The great majority of values are from female patients.

***Race =>>*** The great majority of values are from Caucasian patients.

***Ethnicity =>>*** The great majority of vlaues are from Not Hispanic patients.

***Region =>>*** There were observed more patients classified as Non-Persistent from the Midwest, followed by South, West and Northeast, in descending order. However, when considering patients classified as Persistent, most of patients were from the South, followed by Midwest, West and Northeast, in descending order.

***Age_Bucket =>>*** Most of patients were older than 75 years old, decreasing the number of patients with the decrease of patient's age.

***Ntm_Speciality =>>*** This variable presents too many classes (36), and about half of the values are classified in the class General Practioner (1535), followed by Rheumatology (604) and Endocrinology (458). This variable also presents 310 unkown registers.

***Ntm_Specialist_Flag =>>*** About 50% of patients classified as Persistent were attended by specialists, whereas only 35% of patients classified as Non-Persistent were attended by specialists. This variable might be correlated with the Ntm_Speciality as they bring the same information categorized in two different ways (more specific or broad). 

***Ntm_Speciality_Bucket =>>*** This variable presents another classification of specialities and might also be correlated with the previous two variables.

***Gluco_Record_Prior_Ntm =>>*** Independently of the target class, most of patients did not present Gluco Record prior Ntm.

***Gluco_Record_During_Ntm =>>*** The proportion of patients with Gluco record during RX was lower compared to the proportion of patients withoug Gluco record prior RX for patients classified as Non-Persitent. On the other hand, for patients classified as Persistent, there was a higher propotion of patients with Gluco record during RX compared to Gluco record prior RX.

***Dexa_During_Rx =>>*** The great majority of patients classified as Non-Persistent did not have Dexa during RX, however for patients classified as Persistent, there were more patients that had Dexa during RX compared to patients that did not have Dexa during RX. This variable may be very important for the modeling steps.

***Frag_Frac_Before_Ntm =>>*** Independently of the target classes, most of patients did not have Frag_Frac_Before_Ntm.

***Frag_Frac_During_Ntm =>>*** Similar behaviour of previous variable.

***Risk_Segment_Prior_Ntm =>>*** There was observed a slightly higher number of patients with VLR-LR compared to patients with HR-VHR for both classes of the target variable.

***TScore_Bucket_Prior_Ntm =>>*** Similar behaviour of previous variable.

***Risk_Segment_During_RX =>>*** There were observed very similar counts for patients with VLR-LR or HR-VHR during RX. However, there were a considerable number of unkown values, especially for the class Non-Persistent.

***TScore_Bucket_During_Ntm =>>*** This variable also presented similar count of patients with <=2.5 or >2.5 for the TScore_bucket_During_Ntm. But, similary to the previous variable, there were observed a considerable number of unkown values

***Change_TScore =>>*** This variable presents 4 categories. Considering the patients classified as Non-Persistent, most values are unkown. Witin the known values, most patients presented no change in the TScore change, followed by patients that presented worse results and patients that presented some kind of improvement. For the patients classified as Persistent, most values were observed for patients that did not present any change in the TScore, followed by patients with unkown results. There are a lot of unkown results for this variable.

***Change_Risk_Segment =>>*** Most of the values are unkown for both target classes. Within the known values, most of them were for patients that did not present any change in the Risk Segment, followed by patients that worsen the Change_Risk_Segment. Finally, the category for improved patients was the one that presented less patients.

#### It is important to note that the variables related to Risk_Segment as well as to TScore might be correlated and present colinearity problems

***Adherent_Flag =>>*** Most of patients presented Adherent flag. Moreover, it was observed that there was a higher proportion of non-adherent flag among patients that were classified as Persistent.

***Idn_Indicator =>>*** Most patients from both target classes presented higher positive results. Furthermore, there was observed a higher proportion of positive results among patients classified as Persistent.

***Injectable_Experience_During_RX =>>*** Most of patients from both taget classes presented a much higher number of positive results.

***Comorb_Encounter_For_Screening_For_Malignant_Neoplasms =>>*** This variable presents some very interesting results. Among patients classifed as Non-Persistent, most of them presented negative results for this variable (approximately double). On the other hand, for patients that were classified as Persistent, there were observed more patients with positive result for this variable (approximately double).

***Comorb_Encounter_For_Immunization =>>*** A very similar pattern with the previous variable was observed.

***Comorb_Encntr_For_General_Exam_W_O_Complaint,_Susp_Or_Reprtd_Dx =>>*** Again, it was observed a higher number of negative results for patients classified as Non-Persistent. But, there were more patients with positive results among the ones classified as Persistent.

***Comorb_Vitamin_D_Deficiency =>>*** This variable presented higher number of patients with negative results for both target classes. However, when comparing the patients classified as Non-Persistent and Persitent, it was observed a higher proportion of negative results for the Non-Persistent ones.

***Comorb_Other_Joint_Disorder_Not_Elsewhere_Classified =>>*** Similar behaviour as the previous variable.

***Comorb_Encntr_For_Oth_Sp_Exam_W_O_Complaint_Suspected_Or_Reprtd_Dx =>>*** Similar behaviour as the previous variable.

***Comorb_Long_Term_Current_Drug_Therapy =>>*** Similar behaviour as the previous variable.

***Comorb_Dorsalgia =>>*** Similar behaviour as the previous variable.

***Comorb_Personal_History_Of_Other_Diseases_And_Conditions =>>*** Similar behaviour as the previous variable.

***Comorb_Other_Disorders_Of_Bone_Density_And_Structure =>>*** Similar behaviour as the previous variable.

***Comorb_Disorders_of_lipoprotein_metabolism_and_other_lipidemias =>>*** This variable presented higher number of negative values for the Non-Persistent patients but higher number of positive values for the Persistent patients. This variable may be important for the modeling steps.

***Comorb_Osteoporosis_without_current_pathological_fracture =>>*** Similar behaviour as the variable Comorb_Other_Disorders_Of_Bone_Density_And_Structure.

***Comorb_Personal_history_of_malignant_neoplasm =>>*** Similar behaviour as the previous variable.

***Comorb_Gastro_esophageal_reflux_disease =>>*** Similar behaviour as the previous variable.

***Concom_Cholesterol_And_Triglyceride_Regulating_Preparations =>>*** There are more negative values for both target classes, however, there is a higher proportion of negative values for the Non-Persistent class.

***Concom_Narcotics =>>*** Similar behaviour as the previous variable.

***Concom_Systemic_Corticosteroids_Plain =>>*** Similar behaviour as the previous variable.

***Concom_Anti_Depressants_And_Mood_Stabilisers =>>*** Similar behaviour as the previous variable.

***Concom_Fluoroquinolones =>>*** Similar behaviour as the previous variable.

***Concom_Cephalosporins =>>*** Similar behaviour as the previous variable.

***Concom_Macrolides_And_Similar_Types =>>*** Similar behaviour as the previous variable.

***Concom_Broad_Spectrum_Penicillins =>>*** Similar behaviour as the previous variable.

***Concom_Anaesthetics_General =>>*** Similar behaviour as the previous variable.

***Concom_Viral_Vaccines =>>*** Similar behaviour as the previous variable, however with more extreme proportions.

***Risk_Type_1_Insulin_Dependent_Diabetes =>>*** There were much more negative results for both target classes, and the proportion does not seems to be very discrepant.

***Risk_Osteogenesis_Imperfecta =>>*** This variable presents only 3 positive results and will be removed for the modeling steps.

***Risk_Rheumatoid_Arthritis =>>*** There were higher number of negative results for both target classes. There was a slight higher number of patients with negative results in the class Non-Persistents.

***Risk_Untreated_Chronic_Hyperthyroidism =>>*** This variable presents only 2 positive results and will be removed for the modeling steps.

***Risk_Untreated_Chronic_Hypogonadism =>>*** Similar behaviour as the variable Risk_Rheumatoid_Arthritis

***Risk_Untreated_Early_Menopause =>>*** This variable presents only 12 positive results and will be removed for the modeling steps.

***Risk_Patient_Parent_Fractured_Their_Hip =>>*** This variable presented much more negative results for both target classes and the proportion seems to very similar.

***Risk_Smoking_Tobacco =>>*** There were observed more negative results for both target classes and it seems that there were a slightly higher proportion of negative results for the Non-Persistent patients.

***Risk_Chronic_Malnutrition_Or_Malabsorption =>>*** Similar behaviour as the previous variable.

***Risk_Chronic_Liver_Disease =>>*** This variable presents only 18 positive results, which are spread over the Non-Persistent and Persistent patients, and will be removed for the modeling steps.

***Risk_Family_History_Of_Osteoporosis =>>*** A higher number of patients with negative results were observed for both target classes. The proportion of negative results does not seems to be considerably different for patients classified as Persistent and Non-Persisten.

***Risk_Low_Calcium_Intake =>>*** This variable also presents a very low number of values (42) and will also be removed before the modeling steps.

***Risk_Vitamin_D_Insufficiency =>>*** There was a slight higher number of negative results among the patients classified as Non-Persistent, but there was a slight higher number of positive results among the Persistent patients. This variable may also be important for the model.

***Risk_Poor_Health_Frailty =>>*** This variable also presents much more negative results for both target classes and the proportion of negative results seems to be very similar.

***Risk_Excessive_Thinness =>>*** Similar behaviour with the previous variable, however there are just a few positive results in total.

***Risk_Hysterectomy_Oophorectomy =>>*** Similar behaviour with the previous variable, however there are just a few positive results in total.

***Risk_Estrogen_Deficiency =>>*** This variable presents only 11 positive results and will be removed for the modeling steps.

***Risk_Immobilization =>>*** This variable presents only 14 positive results and will be removed for the modeling steps.

***Risk_Recurring_Falls =>>*** Similar behaviour with the variable Risk_Hysterectomy_Oophorectomy

***8. Numerical Variable Descriptive and Correlation Analysis***

The z-test statistical test is performed to check the correlation between numerical based features and the output label(Persistency_Flag). Before this, we treated outliers using 3 approaches and each of these has to be picked and tested against z-test to find out which one is more effective for feature selection and model training.


In [57]:
# Creating a dataframe that holds the target and the numerical variables after transformations
# based on approaches 1 and 2
dataset_combined_approach_1_2 = pd.concat([df['Persistency_Flag'],
                      df1[['Dexa_Freq_During_Rx', 'Count_Of_Risks']],
                      df2[['Dexa_Freq_During_Rx', 'Count_Of_Risks']]],
                     axis=1)
dataset_combined_approach_1_2.columns = ['Persistency_Flag', 'Dexa_Freq_During_Rx1',
                    'Count_Of_Risks1', 'Dexa_Freq_During_Rx2', 'Count_Of_Risks2']

In [58]:
# Creating a dataframe that holds the target and the numerical variables after removal of outliers (approach 3)
df_num3 = df3[['Persistency_Flag', 'Dexa_Freq_During_Rx', 'Count_Of_Risks']]
df_num3.columns = ['Persistency_Flag', 'Dexa_Freq_During_Rx3', 'Count_Of_Risks3']
df_num3['Persistency_Flag'] = df_num3['Persistency_Flag'].astype(str)

C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\3491174905.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_num3['Persistency_Flag'] = df_num3['Persistency_Flag'].astype(str)


* Approach 1 and 2

In [59]:
# Ploting histograms for the variables 'Dexa_Freq_During_Rx1', 'Count_Of_Risks1',
# 'Dexa_Freq_During_Rx2', 'Count_Of_Risks2'
fig, axes = plt.subplots(2,2) # create figure and axes
fig.set_size_inches(18.5, 14)
for i, el in enumerate(list(dataset_combined_approach_1_2.iloc[:,1:].columns.values)):
    
    sns.histplot(data=dataset_combined_approach_1_2,x=el,ax=axes.flatten()[i])




In [60]:
# Ploting the boxplot for the 'Dexa_Freq_During_Rx1' considering the target variables
grouped_data=dataset_combined_approach_1_2[['Persistency_Flag', 'Dexa_Freq_During_Rx1']].groupby('Persistency_Flag')
sns.boxplot(data=dataset_combined_approach_1_2,x=grouped_data.get_group('Persistent')['Dexa_Freq_During_Rx1'])
plt.show()
sns.boxplot(data=dataset_combined_approach_1_2,x=grouped_data.get_group('Non-Persistent')['Dexa_Freq_During_Rx1'])
plt.show()



C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\1697524722.py:4: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()
C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\1697524722.py:6: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [61]:
# Checking the correlation between the target variable and 'Dexa_Freq_During_Rx1 using Z-test'
print(ttest_ind(dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Non-Persistent']['Dexa_Freq_During_Rx1'],
          dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Persistent']['Dexa_Freq_During_Rx1']))
ztest(dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Non-Persistent']['Dexa_Freq_During_Rx1'],
          dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Persistent']['Dexa_Freq_During_Rx1'], value=0) 
# After applying both statistical tests it is clear that scores of both tests are same but p-values does differ a bit but not much ans also p-value of z-test is 0.0 which is totally valid as if the number is too small to display or too many decimal places leads machine to print 0.0

Ttest_indResult(statistic=-40.20244522667013, pvalue=8.627043922462976e-290)


(-40.20244522667013, 0.0)

In [62]:
# Ploting the boxplot for the 'Dexa_Freq_During_Rx2' considering the target variables
grouped_data=dataset_combined_approach_1_2[['Persistency_Flag', 'Dexa_Freq_During_Rx2']].groupby('Persistency_Flag')
sns.boxplot(data=dataset_combined_approach_1_2,x=grouped_data.get_group('Persistent')['Dexa_Freq_During_Rx2'])
plt.show()
sns.boxplot(data=dataset_combined_approach_1_2,x=grouped_data.get_group('Non-Persistent')['Dexa_Freq_During_Rx2'])
plt.show()


C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\825981129.py:4: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()
C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\825981129.py:6: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [63]:
# Checking the correlation between the target variable and 'Dexa_Freq_During_Rx2'
print(ttest_ind(dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Non-Persistent']['Dexa_Freq_During_Rx2'],
          dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Persistent']['Dexa_Freq_During_Rx2']))
ztest(dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Non-Persistent']['Dexa_Freq_During_Rx2'],
          dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Persistent']['Dexa_Freq_During_Rx2'], value=0) 

# After applying both statistical tests it is clear that scores of both tests are same but p-values does differ a bit but not much ans also p-value of z-test is 0.0 which is totally valid as if the number is too small to display or too many decimal places leads machine to print 0.0

Ttest_indResult(statistic=-38.91637243657572, pvalue=1.2776110404028375e-274)


(-38.91637243657572, 0.0)

In [64]:
# Ploting the boxplot for the 'Count_Of_Risks1' considering the target variables

grouped_data=dataset_combined_approach_1_2[['Persistency_Flag', 'Count_Of_Risks1']].groupby('Persistency_Flag')
sns.boxplot(data=dataset_combined_approach_1_2,x=grouped_data.get_group('Persistent')['Count_Of_Risks1'])
plt.show()
sns.boxplot(data=dataset_combined_approach_1_2,x=grouped_data.get_group('Non-Persistent')['Count_Of_Risks1'])
plt.show()



C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2023688259.py:5: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()
C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2023688259.py:7: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [65]:
# Checking the correlation between the target variable and 'Dexa_Freq_During_Rx1 using t-test and Z-test'
print(ttest_ind(dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Non-Persistent']['Count_Of_Risks1'],
          dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Persistent']['Count_Of_Risks1']))
ztest(dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Non-Persistent']['Count_Of_Risks1'],
          dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Persistent']['Count_Of_Risks1'], value=0) 
# In case of count_of_risks from approach 1 it is clear that the p-value is more than 0.05 so in first approach may be it is weakly correlated with persistency_flag

Ttest_indResult(statistic=-1.579679045206944, pvalue=0.11427280962660341)


(-1.579679045206944, 0.11418038684301744)

In [66]:
# Ploting the boxplot for the 'Count_Of_Risks2' considering the target variables
grouped_data=dataset_combined_approach_1_2[['Persistency_Flag', 'Count_Of_Risks2']].groupby('Persistency_Flag')
sns.boxplot(data=dataset_combined_approach_1_2,x=grouped_data.get_group('Persistent')['Count_Of_Risks2'])
plt.show()
sns.boxplot(data=dataset_combined_approach_1_2,x=grouped_data.get_group('Non-Persistent')['Count_Of_Risks2'])
plt.show()


C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\3720045420.py:4: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()
C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\3720045420.py:6: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [67]:
# Checking the correlation between the target variable and count_of_risks2 using t-test and Z-test'
print(ttest_ind(dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Non-Persistent']['Count_Of_Risks2'],
          dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Persistent']['Count_Of_Risks2']))
ztest(dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Non-Persistent']['Count_Of_Risks2'],
          dataset_combined_approach_1_2[dataset_combined_approach_1_2['Persistency_Flag'] == 'Persistent']['Count_Of_Risks2'], value=0) 
# In case of count_of_risks from approach 2 it is visible that count_of_risks does possess a good correlation with output label. 

Ttest_indResult(statistic=-4.1352457040243795, pvalue=3.630916866195027e-05)


(-4.1352457040243795, 3.54575058903874e-05)

Considering the variable 'Dexa_Freq_During_Rx', it seems that both approaches 1 and 2 produced data that were very correlated with the target variable. On the other hand, for the 'Count_Of_Risks', the transformation made in approach 1 did not produce data that was correlated with the target variable but the transformation made in approach 2 produced data that was correlated with the target.

* Approach 3

In [68]:
# Ploting histograms for the variables 'Dexa_Freq_During_Rx3', 'Count_Of_Risks3',
fig, axes = plt.subplots(2,2) # create figure and axes
fig.set_size_inches(18.5, 14)
for i, el in enumerate(list(dataset_combined_approach_1_2.iloc[:,1:].columns.values)):
    
    sns.histplot(data=dataset_combined_approach_1_2,x=el,ax=axes.flatten()[i])
    


In [69]:
# Ploting the boxplot for the 'Dexa_Freq_During_Rx3' considering the target variables

grouped_data=df_num3[['Persistency_Flag', 'Dexa_Freq_During_Rx3']].groupby('Persistency_Flag')
sns.boxplot(data=df_num3,x=grouped_data.get_group('0')['Dexa_Freq_During_Rx3'])
plt.show()
sns.boxplot(data=df_num3,x=grouped_data.get_group('1')['Dexa_Freq_During_Rx3'])
plt.show()



C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\939304563.py:5: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()
C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\939304563.py:7: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [70]:
# Checking the correlation between the target variable and 'Dexa_Freq_During_Rx3 using T-test and Z-test'
print(ttest_ind(df_num3[df_num3['Persistency_Flag'] == '0']['Dexa_Freq_During_Rx3'],
          df_num3[df_num3['Persistency_Flag'] == '1']['Dexa_Freq_During_Rx3']))
ztest(df_num3[df_num3['Persistency_Flag'] == '0']['Dexa_Freq_During_Rx3'],
          df_num3[df_num3['Persistency_Flag'] == '1']['Dexa_Freq_During_Rx3'],value=0)
# It seems like both has same score value and p-value less than 0.05 

Ttest_indResult(statistic=-28.657591744080833, pvalue=1.0804740149328292e-161)


(-28.657591744080836, 1.2893145885374856e-180)

In [71]:
# Ploting the boxplot for the 'Count_Of_Risks3' considering the target variables
grouped_data=df_num3[['Persistency_Flag', 'Count_Of_Risks3']].groupby('Persistency_Flag')
sns.boxplot(data=df_num3,x=grouped_data.get_group('0')['Count_Of_Risks3'])
plt.show()
sns.boxplot(data=df_num3,x=grouped_data.get_group('1')['Count_Of_Risks3'])
plt.show()



C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2705309175.py:4: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()
C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2705309175.py:6: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [72]:
# Checking the correlation between the target variable and 'Count_Of_Risks3'
print(ttest_ind(df_num3[df_num3['Persistency_Flag'] == '0']['Count_Of_Risks3'],
          df_num3[df_num3['Persistency_Flag'] == '1']['Count_Of_Risks3']))
ztest(df_num3[df_num3['Persistency_Flag'] == '0']['Count_Of_Risks3'],
          df_num3[df_num3['Persistency_Flag'] == '1']['Count_Of_Risks3'],value=0)

Ttest_indResult(statistic=-4.431660783849603, pvalue=9.651388058316117e-06)


(-4.431660783849603, 9.351004635627706e-06)

For the dataset transformed by removing the outliers, there were still a very significant correlation between 'Dexa_Freq_During_Rx' and the target variable. The 'Count_Of_Risks' variable also presented a significant correlation with the target variable.

#### New ideas for transforming the data
It is necessary to make a transformation because outliers can be a problem for the ML algorithms. The variable 'Count_Of_Risks' presented outliers, but, in fact, the outliers are possible values because they represent the sum of the positive results for the risks presented as categorical variables. Some people may have 7 out of all risks presented in the dataset. Therefore, let's try the buckenization of this variable, so that we can still use all the information of the dataset, but grouped in a different way.

In [73]:
# Checking the distribution of the 'Count_Of_Risks' variable
df['Count_Of_Risks'].hist()

<Axes: xlabel='Count_Of_Risks3', ylabel='Count'>

As observed in the previous histogram, most of values are 0, 1 and 2. Therefore, let's group all the values that are higher or equal to 3.

In [74]:
# Creating a new variable with the count of risks buckenized following the rule explained right above
Count_Of_Risks_buckenized_list = []
for i in range(len(df)):
    if df['Count_Of_Risks'].iloc[i] >= 3:
        Count_Of_Risks_buckenized_list.append(3)
    else:
        Count_Of_Risks_buckenized_list.append(df['Count_Of_Risks'].iloc[i])
df['Count_Of_Risks_Buckenized'] = Count_Of_Risks_buckenized_list

In [75]:
# Checking the distribution of the buckenized 'Count_Of_Buckenized'
df['Count_Of_Risks_Buckenized'].hist()

<Axes: xlabel='Count_Of_Risks3', ylabel='Count'>

In [76]:
# Ploting the boxplot for the 'Count_Of_Risks_Buckenized' considering the target variables
df[['Persistency_Flag', 'Count_Of_Risks_Buckenized']].groupby('Persistency_Flag').plot(kind='box')

Persistency_Flag
Non-Persistent    Axes(0.125,0.11;0.775x0.77)
Persistent        Axes(0.125,0.11;0.775x0.77)
dtype: object

In [77]:
# Checking the correlation between the target variable and 'Count_Of_Risks_Buckenized'
print(ttest_ind(df[df['Persistency_Flag'] == 'Non-Persistent']['Count_Of_Risks_Buckenized'],
          df[df['Persistency_Flag'] == 'Persistent']['Count_Of_Risks_Buckenized']))
ztest(df[df['Persistency_Flag'] == 'Non-Persistent']['Count_Of_Risks_Buckenized'],
          df[df['Persistency_Flag'] == 'Persistent']['Count_Of_Risks_Buckenized'],value=0)

Ttest_indResult(statistic=-4.749413973135871, pvalue=2.123838591869459e-06)


(-4.74941397313587, 2.040069549723728e-06)

After all the tests, we can see that the best approach, based on the higher correlation with the target, was this last one, where the variable 'Count_Of_Risks' was buckenized. For the 'Dexa_Freq_During_Rx', the best approach, was the approach 1, which presented the higher correlation with the target. So, let's create the new dataset that will be used for the feature selection steps.

In [78]:
# Creating a dataframe for the following steps of feature selection
df_prep = pd.concat([df1.drop(columns='Count_Of_Risks'), df[['Count_Of_Risks_Buckenized']]], axis=1)

***9. Let's perform a few more tasks in this exploratory analysis to understand a few more details of the dataset.***

* ***Let's first analyse all the Ntm_Speciality variables***

In [79]:
# Visualizing the first and last 5 rows of the dataset, considering only the Ntm_Speciality variables
df[['Ntm_Speciality', 'Ntm_Specialist_Flag', 'Ntm_Speciality_Bucket']]

Ntm_Speciality Ntm_Specialist_Flag      Ntm_Speciality_Bucket
0     GENERAL PRACTITIONER              Others  OB/GYN/Others/PCP/Unknown
1     GENERAL PRACTITIONER              Others  OB/GYN/Others/PCP/Unknown
2     GENERAL PRACTITIONER              Others  OB/GYN/Others/PCP/Unknown
3     GENERAL PRACTITIONER              Others  OB/GYN/Others/PCP/Unknown
4     GENERAL PRACTITIONER              Others  OB/GYN/Others/PCP/Unknown
...                    ...                 ...                        ...
3419  GENERAL PRACTITIONER              Others  OB/GYN/Others/PCP/Unknown
3420               Unknown              Others  OB/GYN/Others/PCP/Unknown
3421         ENDOCRINOLOGY          Specialist               Endo/Onc/Uro
3422               Unknown              Others  OB/GYN/Others/PCP/Unknown
3423               Unknown              Others  OB/GYN/Others/PCP/Unknown

[3424 rows x 3 columns]

In [80]:
# Checking the Ntm_Speciality variabbles
df[['Ntm_Speciality', 'Ntm_Specialist_Flag', 'Ntm_Speciality_Bucket']].nunique()

Ntm_Speciality           36
Ntm_Specialist_Flag       2
Ntm_Speciality_Bucket     3
dtype: int64


These three features represent same information but in broad and short categories so it better to remove 2 out of 3 for model training.

In [81]:
# Checking correlation between all the Ntm_Specialist variables
CrosstabResult1 = pd.crosstab(index=df['Ntm_Speciality_Bucket'], columns=df['Ntm_Speciality'])
ChiSqResult1 = chi2_contingency(CrosstabResult1)
print("p-value: {}".format(ChiSqResult1[1]))

print("*******************************")

CrosstabResult2 = pd.crosstab(index=df_obj['Ntm_Speciality_Bucket'], columns=df_obj['Ntm_Specialist_Flag'])
ChiSqResult2 = chi2_contingency(CrosstabResult2)
print("p-value: {}".format(ChiSqResult2[1]))

print("*******************************")

CrosstabResult3 = pd.crosstab(index=df_obj['Ntm_Speciality'], columns=df_obj['Ntm_Specialist_Flag'])
ChiSqResult3 = chi2_contingency(CrosstabResult3)
print("p-value: {}".format(ChiSqResult3[1]))

p-value: 0.0
*******************************
p-value: 0.0
*******************************
p-value: 0.0


In [82]:
# Visualizing the correlations between 'Ntm_Speciality_Bucket' and 'Ntm_Speciality'
CrosstabResult1.T.plot(kind='bar')

<Axes: xlabel='Ntm_Speciality'>

In [83]:
# Visualizing the correlations between 'Ntm_Speciality_Bucket' and 'Ntm_Specialist_Flag'
CrosstabResult2.plot(kind='bar')

<Axes: xlabel='Ntm_Speciality_Bucket'>

In [84]:
# Visualizing the correlations between 'Ntm_Speciality' and 'Ntm_Specialist_Flag'
CrosstabResult3.plot(kind='bar')

<Axes: xlabel='Ntm_Speciality'>

All the Ntm_Speciality variables are correlated to each other, and therefore one of them should be choosed for the modeling steps. Let's re-check the distribution of these variables again.

In [85]:
# Re-checking the distribution of Ntm_Speciality
df['Ntm_Speciality'].value_counts().plot(kind='bar')

<Axes: xlabel='Ntm_Speciality'>

In [86]:
# Re-checking the distribution of Ntm_Specialist_Flag
df['Ntm_Specialist_Flag'].value_counts().plot(kind='bar')

<Axes: xlabel='Ntm_Speciality'>

In [87]:
# Re-checking the distribution of Ntm_Speciality_Bucket
df['Ntm_Speciality_Bucket'].value_counts().plot(kind='bar')

<Axes: xlabel='Ntm_Speciality'>

Based on the correlation analysis, the variable Ntm_Speciality_Bucket was the one that presented the highest correlation with the target variable, and therefore this variable will be kept and the other two variables will be removed. When testing the models, we can also try to substitute the Ntm_Speciality_Bucket by the Ntm_Speciality_Flag to see how it goes. The latter variable is interesting because it is also well correlated with the target and presents only two categories instead of three. Moreover, the values are more well distributed among the categories.

* ***Let's investigate the correlation between the Dexa_Freq_During_Rx and Dexa_During_Rx***

In [88]:
# Ploting the boxplot for the 'Dexa_Freq_During_Rx' considering the Dexa_During_Rx variable
df10 = df1[['Dexa_During_Rx', 'Dexa_Freq_During_Rx']]
df10['Dexa_During_Rx'] = df10['Dexa_During_Rx'].astype(str)
df10.groupby('Dexa_During_Rx').plot(kind='box')

C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2488862739.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df10['Dexa_During_Rx'] = df10['Dexa_During_Rx'].astype(str)


Dexa_During_Rx
0    Axes(0.125,0.11;0.775x0.77)
1    Axes(0.125,0.11;0.775x0.77)
dtype: object

In [89]:
# Checking the correlation between the Dexa_During_Rx variable and 'Dexa_Freq_During_Rx'
print(ttest_ind(df10[df10['Dexa_During_Rx'] == '0']['Dexa_Freq_During_Rx'],
          df10[df10['Dexa_During_Rx'] == '1']['Dexa_Freq_During_Rx']))
ztest(df10[df10['Dexa_During_Rx'] == '0']['Dexa_Freq_During_Rx'],
          df10[df10['Dexa_During_Rx'] == '1']['Dexa_Freq_During_Rx'],value=0)
# Both showed same results and it seems that both are closely correlated to each other

Ttest_indResult(statistic=-60.25829138015062, pvalue=0.0)


(-60.25829138015061, 0.0)

These variables presented a significant correlation, and therefore, one of them might also be removed during the following steps. As the Dexa_During_Rx presented a more significant correlation with the target variable, it seems to be a good idea to remove the Dexa_Freq_During_Rx, which was the variable that presented outliers that were treated by 3 different approaches.

* ***Let's investigate the unkowns of variables Risk_Segment_During_Rx, Tscore_Bucket_During_Rx, Change_T_Score and Change_Risk_Segment***

In [90]:
# Creating the dataframe to hold the 4 variables that presents a lot of unkown values
df_unkowns = df[['Risk_Segment_During_Rx', 'Tscore_Bucket_During_Rx', 'Change_T_Score', 'Change_Risk_Segment']]

* ***Segment variables analysis***

The variable Risk_Segment_Prior_Ntm did not present a significant correlation with the target and may be excluded in the following steps before modeling. However, let's check if there is a correlation between the Risk_Segment_During_Rx' and 'Change_T_Score variables.

In [91]:
# Checking the number of values for each combination of categories of these variables
df_unkowns[['Risk_Segment_During_Rx', 'Change_Risk_Segment']].value_counts()

Risk_Segment_During_Rx  Change_Risk_Segment
Unknown                 Unknown                1497
HR_VHR                  No change               784
VLR_LR                  Unknown                 683
                        No change               268
HR_VHR                  Worsened                121
                        Unknown                  49
                        Improved                 11
VLR_LR                  Improved                 11
dtype: int64

In [92]:
# Ploting an histogram for the variable Risk_Segment_During_Rx
df_unkowns['Risk_Segment_During_Rx'].hist()
plt.show()

C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\1760158651.py:3: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [93]:
# Ploting an histogram for the variable Change_Risk_Segment
df_unkowns['Change_Risk_Segment'].hist()
plt.show()

C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\1998418865.py:3: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [94]:
# Checking correlation between Risk_Segment_During_Rx and Change_T_Score
CrosstabResult = pd.crosstab(index=df_unkowns['Risk_Segment_During_Rx'], columns=df_unkowns['Change_Risk_Segment'])
ChiSqResult = chi2_contingency(CrosstabResult)
print("p-value: {}".format(ChiSqResult[1]))

p-value: 0.0


As we can see, nearly half of the values are unknown for both variables and correspondents. There are a few more unkown values for the variable Change_Risk_Segment. Moreover, these variables are correlated, and one of them should also be removed. As the variable Risk_Segment_During_Rx presented a more significant correlation with the target, the Change_T_Score variable may be removed. Finally, the Risk_Segment_During_Rx also presents the advantage of having less categories with the values more equaly distribute.

 ***TScore variables analysis ***

Simiary to the Segment group of variable, the variable Tscore_Bucket_Prior_Ntm did not present a significant correlation with the target and may be excluded in the following steps before modeling. However, let's check if there is a correlation between the Tscore_Bucket_During_Rx and Change_T_Score variables.

In [95]:
# Checking the number of values for each combination of categories of these variables
df_unkowns[['Tscore_Bucket_During_Rx', 'Change_T_Score']].value_counts()

Tscore_Bucket_During_Rx  Change_T_Score
Unknown                  Unknown           1497
<=-2.5                   No change          861
>-2.5                    No change          799
<=-2.5                   Worsened           131
>-2.5                    Improved            69
                         Worsened            42
<=-2.5                   Improved            25
dtype: int64

In [96]:
# Ploting an histogram for the variable Tscore_Bucket_During_Rx
df_unkowns['Tscore_Bucket_During_Rx'].hist()
plt.show()

C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2622222051.py:3: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [97]:
# Ploting an histogram for the variable Change_T_Score
df_unkowns['Change_T_Score'].hist()
plt.show()

C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2523823108.py:3: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [98]:
# Checking correlation between Tscore_Bucket_During_Rx and Change_T_Score
CrosstabResult = pd.crosstab(index=df_unkowns['Tscore_Bucket_During_Rx'], columns=df_unkowns['Change_T_Score'])
ChiSqResult = chi2_contingency(CrosstabResult)
print("p-value: {}".format(ChiSqResult[1]))

p-value: 0.0


Similarly to the previous analysis, the variables Tscore_Bucket_During_Rx and Change_T_Score are correlated and one of them has to be removed. The Change_T_Score presented higher correlation with the target variable, however the 4 categories of this variable are not evenly distributed, whereas the variable Tscore_Bucket_During_Rx presented 3 categories with the values better distributed.

In [99]:
# Checking the proportion of unknown values in the combination of these variables
df_unkowns[['Risk_Segment_During_Rx', 'Tscore_Bucket_During_Rx']].value_counts()

Risk_Segment_During_Rx  Tscore_Bucket_During_Rx
Unknown                 Unknown                    1497
HR_VHR                  <=-2.5                      857
VLR_LR                  >-2.5                       802
                        <=-2.5                      160
HR_VHR                  >-2.5                       108
dtype: int64

So, among the 6 variables related to segment and TScore, 2 variables were selected (Risk_Segment_During_Rx, Tscore_Bucket_During_Rx). One of the possibilities to deal with unkown values would be to assing the category "No Change" for these values, but as nearly half of the values are unkown, it may be better to remove these variables too.

* ***Let's investigate 'Gluco_Record_Prior_Ntm' and'Gluco_Record_During_Rx'***

In [100]:
# Creating a new dataframe for gluco variables and checking the grouped count for the Y and N values
df_gluco = df[['Gluco_Record_Prior_Ntm', 'Gluco_Record_During_Rx']]
df_gluco.value_counts()

Gluco_Record_Prior_Ntm  Gluco_Record_During_Rx
N                       N                         2169
Y                       Y                          452
N                       Y                          450
Y                       N                          353
dtype: int64

In [101]:
# Checking correlation between Gluco_Record_Prior_Ntm and Gluco_Record_During_Rx
CrosstabResult = pd.crosstab(index=df_gluco['Gluco_Record_Prior_Ntm'], columns=df_gluco['Gluco_Record_During_Rx'])
ChiSqResult = chi2_contingency(CrosstabResult)
print("p-value: {}".format(ChiSqResult[1]))

p-value: 2.318014555829997e-106


These two variables are very correlated, and therefore, one of them should be removed before the modeling steps. Moreover, the Gluco_Record_Prior_Ntm is not correlated with the target variable. Therefore, we will keep the Gluco_Record_During_Rx for the next steps of the modeling.

* ***Let's investigate 'Frag_Frac_Prior_Ntm' and 'Frag_Frac_During_Rx'***

In [102]:
# Creating a new dataframe for frag_frac variables and checking the grouped count for the Y and N values
df_frag = df[['Frag_Frac_Prior_Ntm', 'Frag_Frac_During_Rx']]
df_frag.value_counts()

Frag_Frac_Prior_Ntm  Frag_Frac_During_Rx
N                    N                      2691
Y                    N                       316
                     Y                       236
N                    Y                       181
dtype: int64

In [103]:
# Checking correlation between Frag_Frac_Prior_Ntm and Frag_Frac_During_Rx
CrosstabResult = pd.crosstab(index=df_frag['Frag_Frac_Prior_Ntm'], columns=df_frag['Frag_Frac_During_Rx'])
ChiSqResult = chi2_contingency(CrosstabResult)
print("p-value: {}".format(ChiSqResult[1]))

p-value: 2.2868443185738897e-126


These two variables are also very correlated, and one of them should be also removed before proceeding with the modeling steps. Similarly to the Gluco variables, the Frag_Frac_Prior_Ntm did not present a correlation with the target variable and will be removed before modeling. Therefore, we will keep the Frag_Frac_Prior_Ntm.

* ***Let's investigate the variables Adherent_Flag, Risk_Type_1_Insulin_Dependent_Diabetes, Risk_Rheumatoid_Arthritis, Risk_Untreated_Chronic_Hypogonadism, Risk_Low_Calcium_Intake, Risk_Poor_Health_Frailty, Risk_Excessive_Thinness, Risk_Hysterectomy_Oophorectomy and Risk_Recurring_Falls***

In [104]:
# Checking correlation between these variables
vars2 = ['Adherent_Flag', 'Risk_Type_1_Insulin_Dependent_Diabetes', 'Risk_Rheumatoid_Arthritis',
         'Risk_Untreated_Chronic_Hypogonadism', 'Risk_Low_Calcium_Intake', 'Risk_Poor_Health_Frailty',
         'Risk_Excessive_Thinness', 'Risk_Hysterectomy_Oophorectomy', 'Risk_Recurring_Falls']

for col in vars2:
    CrosstabResult = pd.crosstab(index=df['Persistency_Flag'], columns=df[col])
    ChiSqResult = chi2_contingency(CrosstabResult)
    print(col)
    print(ChiSqResult[1])
    CrosstabResult.plot(kind='bar')
    plt.plot()
    print('\n****************\n')

Adherent_Flag
7.94091880775299e-11

****************

Risk_Type_1_Insulin_Dependent_Diabetes
0.2975780869378699

****************

Risk_Rheumatoid_Arthritis
0.0022403221153491602

****************

Risk_Untreated_Chronic_Hypogonadism
0.0001126569632109499

****************

Risk_Low_Calcium_Intake
0.6743249891087415

****************

Risk_Poor_Health_Frailty
0.010090616367125695

****************

Risk_Excessive_Thinness
0.026326220250030584

****************

Risk_Hysterectomy_Oophorectomy
0.423194002702869

****************

Risk_Recurring_Falls
0.2612273105944741

****************



From these 9 variables, we can see that only 5 presents some level of correlation with the target variable. Let's investigate problems of colinerity among these 5 variables in the following step.

In [105]:
# Creating a list of variables with the 5 variables identified in the previous cell
vars3 = ['Adherent_Flag', 'Risk_Rheumatoid_Arthritis', 'Risk_Untreated_Chronic_Hypogonadism',
         'Risk_Poor_Health_Frailty', 'Risk_Excessive_Thinness']

In [106]:
# Checking problems of colinearity among these 5 selected variables
p=len(vars3)
for i in range(len(vars3)):
    for j in range(i+1,p):
        CrosstabResult = pd.crosstab(index=df[vars3[i]], columns=df[vars3[j]])
        ChiSqResult = chi2_contingency(CrosstabResult)
        print(vars3[i], '-', vars3[j])
        print(ChiSqResult[1])

Adherent_Flag - Risk_Rheumatoid_Arthritis
0.6627208402559772
Adherent_Flag - Risk_Untreated_Chronic_Hypogonadism
0.7050595565833054
Adherent_Flag - Risk_Poor_Health_Frailty
0.2776673174078582
Adherent_Flag - Risk_Excessive_Thinness
1.0
Risk_Rheumatoid_Arthritis - Risk_Untreated_Chronic_Hypogonadism
0.7483060136591221
Risk_Rheumatoid_Arthritis - Risk_Poor_Health_Frailty
0.6380696141206544
Risk_Rheumatoid_Arthritis - Risk_Excessive_Thinness
0.056329743467166744
Risk_Untreated_Chronic_Hypogonadism - Risk_Poor_Health_Frailty
0.08525229315920102
Risk_Untreated_Chronic_Hypogonadism - Risk_Excessive_Thinness
1.0
Risk_Poor_Health_Frailty - Risk_Excessive_Thinness
0.0020705647327024994


As we can see in the previous correlation analysis, the variable Adherent_Flag is not correlated to any of the other variables related to risk. Most of the other risk variables evaluated in this analysis did not present problems of colinearity. The only variables that presented a significant correlation were Risk_Poor_Health_Frailty and Risk_Excessive_Thinness.

* ***Now, let's have a look in all the risk variables and check how it is correlated to the target variable and also to the Count_Of_Risks variable***.

In [107]:
# Creating a new dataframe to hold all the risk-related variables
df_risks = df[['Risk_Type_1_Insulin_Dependent_Diabetes',
               'Risk_Osteogenesis_Imperfecta', 'Risk_Rheumatoid_Arthritis',
               'Risk_Untreated_Chronic_Hyperthyroidism',
               'Risk_Untreated_Chronic_Hypogonadism', 'Risk_Untreated_Early_Menopause',
               'Risk_Patient_Parent_Fractured_Their_Hip', 'Risk_Smoking_Tobacco',
               'Risk_Chronic_Malnutrition_Or_Malabsorption',
               'Risk_Chronic_Liver_Disease', 'Risk_Family_History_Of_Osteoporosis',
               'Risk_Low_Calcium_Intake', 'Risk_Vitamin_D_Insufficiency',
               'Risk_Poor_Health_Frailty', 'Risk_Excessive_Thinness',
               'Risk_Hysterectomy_Oophorectomy', 'Risk_Estrogen_Deficiency',
               'Risk_Immobilization', 'Risk_Recurring_Falls', 'Count_Of_Risks', 'Persistency_Flag']]

# Creating a new feature to check if the Count_Of_Risks variable is, in fact, the sum of all factor risks.
df_risks['Count_Of_Risks_Check'] = df1[['Risk_Type_1_Insulin_Dependent_Diabetes',
                                       'Risk_Osteogenesis_Imperfecta', 'Risk_Rheumatoid_Arthritis',
                                       'Risk_Untreated_Chronic_Hyperthyroidism',
                                       'Risk_Untreated_Chronic_Hypogonadism', 'Risk_Untreated_Early_Menopause',
                                       'Risk_Patient_Parent_Fractured_Their_Hip', 'Risk_Smoking_Tobacco',
                                       'Risk_Chronic_Malnutrition_Or_Malabsorption',
                                       'Risk_Chronic_Liver_Disease', 'Risk_Family_History_Of_Osteoporosis',
                                       'Risk_Low_Calcium_Intake', 'Risk_Vitamin_D_Insufficiency',
                                       'Risk_Poor_Health_Frailty', 'Risk_Excessive_Thinness',
                                       'Risk_Hysterectomy_Oophorectomy', 'Risk_Estrogen_Deficiency',
                                       'Risk_Immobilization', 'Risk_Recurring_Falls']].sum(axis=1)

# Visualizing the new dataframe with risks variables
df_risks.head()

C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\3493344861.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_risks['Count_Of_Risks_Check'] = df1[['Risk_Type_1_Insulin_Dependent_Diabetes',


Risk_Type_1_Insulin_Dependent_Diabetes Risk_Osteogenesis_Imperfecta  \
0                                      N                            N   
1                                      N                            N   
2                                      N                            N   
3                                      N                            N   
4                                      N                            N   

  Risk_Rheumatoid_Arthritis Risk_Untreated_Chronic_Hyperthyroidism  \
0                         N                                      N   
1                         N                                      N   
2                         N                                      N   
3                         N                                      N   
4                         N                                      N   

  Risk_Untreated_Chronic_Hypogonadism Risk_Untreated_Early_Menopause  \
0                                   N                              N   
1                                   N                              N   
2                                   N                              N   
3                                   N                              N   
4                                   N                              N   

  Risk_Patient_Parent_Fractured_Their_Hip Risk_Smoking_Tobacco  \
0                                       N                    N   
1                                       N                    N   
2                                       Y                    N   
3                                       N                    Y   
4                                       N                    Y   

  Risk_Chronic_Malnutrition_Or_Malabsorption Risk_Chronic_Liver_Disease  ...  \
0                                          N                          N  ...   
1                                          N                          N  ...   
2                                          N                          N  ...   
3                                          N                          N  ...   
4                                          N                          N  ...   

  Risk_Vitamin_D_Insufficiency Risk_Poor_Health_Frailty  \
0                            N                        N   
1                            N                        N   
2                            N                        N   
3                            N                        N   
4                            N                        N   

  Risk_Excessive_Thinness Risk_Hysterectomy_Oophorectomy  \
0                       N                              N   
1                       N                              N   
2                       N                              N   
3                       N                              N   
4                       N                              N   

  Risk_Estrogen_Deficiency Risk_Immobilization Risk_Recurring_Falls  \
0                        N                   N                    N   
1                        N                   N                    N   
2                        N                   N                    N   
3                        N                   N                    N   
4                        N                   N                    N   

  Count_Of_Risks Persistency_Flag  Count_Of_Risks_Check  
0              0       Persistent                     0  
1              0   Non-Persistent                     0  
2              2   Non-Persistent                     2  
3              1   Non-Persistent                     1  
4              1   Non-Persistent                     1  

[5 rows x 22 columns]

In [108]:
# Checking if Count_Of_Risks and Count_Of_Risks_Check are exactly the same
df_risks['Count_Of_Risks'].equals(df_risks['Count_Of_Risks_Check'])

True

As we can see, these variables are exactly the same. In this case, let's remove these variables and check which of these risk variables are correlated with the target. Selecting only the variables that are correlated with the target, we can make a colinearity analysis to check if some variables present similar information. If so, we can also exclude one of the colinear variables. Finally, we can create a new Count_Of_Risks based on the sum of the selected risk varialbes.

In [109]:
# Removing the variables Count_Of_Risks_Check and Count_Of_Risks and visualizing the dataset
df_risks.drop(columns=['Count_Of_Risks_Check', 'Count_Of_Risks'], inplace=True)
df_risks.head()

C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2354697127.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_risks.drop(columns=['Count_Of_Risks_Check', 'Count_Of_Risks'], inplace=True)


Risk_Type_1_Insulin_Dependent_Diabetes Risk_Osteogenesis_Imperfecta  \
0                                      N                            N   
1                                      N                            N   
2                                      N                            N   
3                                      N                            N   
4                                      N                            N   

  Risk_Rheumatoid_Arthritis Risk_Untreated_Chronic_Hyperthyroidism  \
0                         N                                      N   
1                         N                                      N   
2                         N                                      N   
3                         N                                      N   
4                         N                                      N   

  Risk_Untreated_Chronic_Hypogonadism Risk_Untreated_Early_Menopause  \
0                                   N                              N   
1                                   N                              N   
2                                   N                              N   
3                                   N                              N   
4                                   N                              N   

  Risk_Patient_Parent_Fractured_Their_Hip Risk_Smoking_Tobacco  \
0                                       N                    N   
1                                       N                    N   
2                                       Y                    N   
3                                       N                    Y   
4                                       N                    Y   

  Risk_Chronic_Malnutrition_Or_Malabsorption Risk_Chronic_Liver_Disease  \
0                                          N                          N   
1                                          N                          N   
2                                          N                          N   
3                                          N                          N   
4                                          N                          N   

  Risk_Family_History_Of_Osteoporosis Risk_Low_Calcium_Intake  \
0                                   N                       N   
1                                   N                       N   
2                                   N                       Y   
3                                   N                       N   
4                                   N                       N   

  Risk_Vitamin_D_Insufficiency Risk_Poor_Health_Frailty  \
0                            N                        N   
1                            N                        N   
2                            N                        N   
3                            N                        N   
4                            N                        N   

  Risk_Excessive_Thinness Risk_Hysterectomy_Oophorectomy  \
0                       N                              N   
1                       N                              N   
2                       N                              N   
3                       N                              N   
4                       N                              N   

  Risk_Estrogen_Deficiency Risk_Immobilization Risk_Recurring_Falls  \
0                        N                   N                    N   
1                        N                   N                    N   
2                        N                   N                    N   
3                        N                   N                    N   
4                        N                   N                    N   

  Persistency_Flag  
0       Persistent  
1   Non-Persistent  
2   Non-Persistent  
3   Non-Persistent  
4   Non-Persistent

In [110]:
# Checking correlation between the risk related variables and target
for col in df_risks.columns[:-1]:
    CrosstabResult = pd.crosstab(index=df_risks['Persistency_Flag'], columns=df_risks[col])
    ChiSqResult = chi2_contingency(CrosstabResult)
    print(col)
    print(ChiSqResult[1])
    CrosstabResult.plot(kind='bar')
    plt.plot()
    print('\n****************\n')

Risk_Type_1_Insulin_Dependent_Diabetes
0.2975780869378699

****************

Risk_Osteogenesis_Imperfecta
1.0

****************

Risk_Rheumatoid_Arthritis
0.0022403221153491602

****************

Risk_Untreated_Chronic_Hyperthyroidism
0.7119516131910122

****************

Risk_Untreated_Chronic_Hypogonadism
0.0001126569632109499

****************

Risk_Untreated_Early_Menopause
0.9916549347059234

****************

Risk_Patient_Parent_Fractured_Their_Hip
0.6750320656266102

****************

Risk_Smoking_Tobacco
1.2559762490212159e-08

****************

Risk_Chronic_Malnutrition_Or_Malabsorption
0.004724259614912723

****************

Risk_Chronic_Liver_Disease
0.4004714776102025

****************

Risk_Family_History_Of_Osteoporosis
0.8833498853663122

****************

Risk_Low_Calcium_Intake
0.6743249891087415

****************

Risk_Vitamin_D_Insufficiency
3.60143371476215e-06

****************

Risk_Poor_Health_Frailty
0.010090616367125695

****************

Risk_Excessive_Thinnes

Only 8 out of 19 risk variables presented some significant level of correlation with the target variable. Now, let's check if there are any problems of correlation among these 8 variables.

In [111]:
# Creating a new dataframe to hold only the 8 variables that presented correlation with the target
df_risks2 = df_risks[['Risk_Rheumatoid_Arthritis', 'Risk_Untreated_Chronic_Hypogonadism', 'Risk_Smoking_Tobacco',
                      'Risk_Chronic_Malnutrition_Or_Malabsorption', 'Risk_Vitamin_D_Insufficiency',
                      'Risk_Poor_Health_Frailty', 'Risk_Excessive_Thinness', 'Risk_Immobilization']]

In [112]:
# Checking problems of colinearity between the risk variables
p=len(df_risks2.columns)
for i in range(len(df_risks2.columns)):
    for j in range(i+1,p):
        CrosstabResult = pd.crosstab(index=df_risks2[df_risks2.columns[i]], columns=df_risks2[df_risks2.columns[j]])
        ChiSqResult = chi2_contingency(CrosstabResult)
        print(df_risks2.columns[i], '-', df_risks2.columns[j])
        print(ChiSqResult[1])

Risk_Rheumatoid_Arthritis - Risk_Untreated_Chronic_Hypogonadism
0.7483060136591221
Risk_Rheumatoid_Arthritis - Risk_Smoking_Tobacco
0.2479479363797091
Risk_Rheumatoid_Arthritis - Risk_Chronic_Malnutrition_Or_Malabsorption
0.7267940793428149
Risk_Rheumatoid_Arthritis - Risk_Vitamin_D_Insufficiency
0.33499931894205454
Risk_Rheumatoid_Arthritis - Risk_Poor_Health_Frailty
0.6380696141206544
Risk_Rheumatoid_Arthritis - Risk_Excessive_Thinness
0.056329743467166744
Risk_Rheumatoid_Arthritis - Risk_Immobilization
0.9647454944977487
Risk_Untreated_Chronic_Hypogonadism - Risk_Smoking_Tobacco
0.4030749310496502
Risk_Untreated_Chronic_Hypogonadism - Risk_Chronic_Malnutrition_Or_Malabsorption
0.110867665483348
Risk_Untreated_Chronic_Hypogonadism - Risk_Vitamin_D_Insufficiency
0.03238340517412947
Risk_Untreated_Chronic_Hypogonadism - Risk_Poor_Health_Frailty
0.08525229315920102
Risk_Untreated_Chronic_Hypogonadism - Risk_Excessive_Thinness
1.0
Risk_Untreated_Chronic_Hypogonadism - Risk_Immobilization

According to the colinearity analysis for the risk variables, the variable Risk_Rheumatoid_Arthritis is not correlated with any other risk variable, considering the 8 selected ones. The variable Risk_Untreated_Chronic_Hypogonadism is only correlated with the variable Risk_Vitamin_D_Insufficiency (p-value=0.03). The Risk_Smoking_Tobacco presented strong correlation with the variables Risk_Chronic_Malnutrition_Or_Malabsorption, Risk_Vitamin_D_Insufficiency and Risk_Poor_Health_Frailty. Moreover, the Risk_Chronic_Malnutrition_Or_Malabsorption is also correlated with the Risk_Vitamin_D_Insufficiency and the Risk_Poor_Health_Frailty correlated with Risk_Excessive_Thinness and Risk_Immobilization.
Based on this, these would be one of the choices for the variables: 'Risk_Rheumatoid_Arthritis', 'Risk_Untreated_Chronic_Hypogonadism', 'Risk_Smoking_Tobacco', 'Risk_Excessive_Thinness', 'Risk_Immobilization'

In [113]:
# Creating a new dataframe to hold only the selected risk variables
df_risks3 = df_risks[['Risk_Rheumatoid_Arthritis', 'Risk_Untreated_Chronic_Hypogonadism', 'Risk_Smoking_Tobacco',
'Risk_Excessive_Thinness', 'Risk_Immobilization', 'Persistency_Flag']]

# Calculating the Count_Of_Risks_New, based only in the selected variables
df_risks3['Count_Of_Risks_New'] = df1[['Risk_Rheumatoid_Arthritis', 'Risk_Untreated_Chronic_Hypogonadism', 'Risk_Smoking_Tobacco',
'Risk_Excessive_Thinness', 'Risk_Immobilization']].sum(axis=1)

# Visualizing the min and max values and the new dataframe
print('Min:', df_risks3['Count_Of_Risks_New'].min(), '\nMax:', df_risks3['Count_Of_Risks_New'].max())
df_risks3.head()

Min: 0 
Max: 3


C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2636948000.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_risks3['Count_Of_Risks_New'] = df1[['Risk_Rheumatoid_Arthritis', 'Risk_Untreated_Chronic_Hypogonadism', 'Risk_Smoking_Tobacco',


Risk_Rheumatoid_Arthritis Risk_Untreated_Chronic_Hypogonadism  \
0                         N                                   N   
1                         N                                   N   
2                         N                                   N   
3                         N                                   N   
4                         N                                   N   

  Risk_Smoking_Tobacco Risk_Excessive_Thinness Risk_Immobilization  \
0                    N                       N                   N   
1                    N                       N                   N   
2                    N                       N                   N   
3                    Y                       N                   N   
4                    Y                       N                   N   

  Persistency_Flag  Count_Of_Risks_New  
0       Persistent                   0  
1   Non-Persistent                   0  
2   Non-Persistent                   0  
3   Non-Persistent                   1  
4   Non-Persistent                   1

In [114]:
# Ploting the boxplot for the 'Count_Of_Risks_New' considering the target variables
df_risks3[['Persistency_Flag', 'Count_Of_Risks_New']].groupby('Persistency_Flag').plot(kind='box')

Persistency_Flag
Non-Persistent    Axes(0.125,0.11;0.775x0.77)
Persistent        Axes(0.125,0.11;0.775x0.77)
dtype: object

In [115]:
# Checking the correlation between the target variable and 'Count_Of_Risks_New'
ttest_ind(df_risks3[df_risks3['Persistency_Flag'] == 'Non-Persistent']['Count_Of_Risks_New'],
          df_risks3[df_risks3['Persistency_Flag'] == 'Persistent']['Count_Of_Risks_New'])

Ttest_indResult(statistic=-6.0911836207861265, pvalue=1.245097030120743e-09)

Following the transformation of the categorical variables related to risk and the new calculation for the Count_Of_Risks, the correlation between the Count_Of_Risks and the target variable has increased, as the p-value decreased from e-06 to e-09.

However, during the modeling steps, it is a good idea to remove all risk related vars and test the numerical Count of Risk New, and also to try to use only these last 5 chosen categorical vars.

Moreover, let's check the correlation between the new Count of Risks variable and the 5 selected categorical vars, so that if some of them are not correlated with the count of risk, these might be used with the Count of Risk as well.

In [116]:
# Checking the correlation between the selected risk variables and 'Count_Of_Risks_New'
for col in df_risks3.columns[:5]:
    a = ttest_ind(df_risks3[df_risks3[col] == 'N']['Count_Of_Risks_New'],
              df_risks3[df_risks3[col] == 'Y']['Count_Of_Risks_New'])
    print(a)

Ttest_indResult(statistic=-25.91774315557377, pvalue=2.207187595807838e-135)
Ttest_indResult(statistic=-24.394979950419422, pvalue=2.5378858353711903e-121)
Ttest_indResult(statistic=-75.41122848157876, pvalue=0.0)
Ttest_indResult(statistic=-18.53023524347137, pvalue=3.9792152746703186e-73)
Ttest_indResult(statistic=-6.887724223249874, pvalue=6.7179857005499815e-12)


As expected, the selected 5 categorical variables are all correlated with the new count of risks variable. In this case, we use only the categorical variables or the numeric when creating the models.

* ***Now, let's have a look in all the Comorb variables and check how it is correlated to the target variable and evaluate colinearity problems.***

# COMORB

In [117]:
# Creating a new dataframe to hold all the Comorb-related variables
df_comorb = df[['Persistency_Flag', 'Comorb_Encounter_For_Screening_For_Malignant_Neoplasms',
       'Comorb_Encounter_For_Immunization',
       'Comorb_Encntr_For_General_Exam_W_O_Complaint,_Susp_Or_Reprtd_Dx',
       'Comorb_Vitamin_D_Deficiency',
       'Comorb_Other_Joint_Disorder_Not_Elsewhere_Classified',
       'Comorb_Encntr_For_Oth_Sp_Exam_W_O_Complaint_Suspected_Or_Reprtd_Dx',
       'Comorb_Long_Term_Current_Drug_Therapy', 'Comorb_Dorsalgia',
       'Comorb_Personal_History_Of_Other_Diseases_And_Conditions',
       'Comorb_Other_Disorders_Of_Bone_Density_And_Structure',
       'Comorb_Disorders_of_lipoprotein_metabolism_and_other_lipidemias',
       'Comorb_Osteoporosis_without_current_pathological_fracture',
       'Comorb_Personal_history_of_malignant_neoplasm',
       'Comorb_Gastro_esophageal_reflux_disease']]

# Visualizing the new comorb dataframe
df_comorb.head()

Persistency_Flag Comorb_Encounter_For_Screening_For_Malignant_Neoplasms  \
0       Persistent                                                  N       
1   Non-Persistent                                                  N       
2   Non-Persistent                                                  Y       
3   Non-Persistent                                                  N       
4   Non-Persistent                                                  Y       

  Comorb_Encounter_For_Immunization  \
0                                 Y   
1                                 N   
2                                 N   
3                                 Y   
4                                 Y   

  Comorb_Encntr_For_General_Exam_W_O_Complaint,_Susp_Or_Reprtd_Dx  \
0                                                  Y                
1                                                  Y                
2                                                  Y                
3                                                  Y                
4                                                  Y                

  Comorb_Vitamin_D_Deficiency  \
0                           N   
1                           N   
2                           N   
3                           N   
4                           N   

  Comorb_Other_Joint_Disorder_Not_Elsewhere_Classified  \
0                                                  N     
1                                                  N     
2                                                  N     
3                                                  Y     
4                                                  N     

  Comorb_Encntr_For_Oth_Sp_Exam_W_O_Complaint_Suspected_Or_Reprtd_Dx  \
0                                                  Y                   
1                                                  N                   
2                                                  N                   
3                                                  N                   
4                                                  N                   

  Comorb_Long_Term_Current_Drug_Therapy Comorb_Dorsalgia  \
0                                     N                Y   
1                                     N                N   
2                                     N                N   
3                                     N                Y   
4                                     N                Y   

  Comorb_Personal_History_Of_Other_Diseases_And_Conditions  \
0                                                  Y         
1                                                  N         
2                                                  N         
3                                                  N         
4                                                  Y         

  Comorb_Other_Disorders_Of_Bone_Density_And_Structure  \
0                                                  N     
1                                                  N     
2                                                  N     
3                                                  N     
4                                                  N     

  Comorb_Disorders_of_lipoprotein_metabolism_and_other_lipidemias  \
0                                                  N                
1                                                  N                
2                                                  N                
3                                                  Y                
4                                                  N                

  Comorb_Osteoporosis_without_current_pathological_fracture  \
0                                                  N          
1                                                  N          
2                                                  N          
3                                                  N          
4                                                  N          

  Comorb_Personal_history_of_ma

In [118]:
# Checking correlation between the comorb related variables and target
for col in df_comorb.columns[1:]:
    CrosstabResult = pd.crosstab(index=df_comorb['Persistency_Flag'], columns=df_comorb[col])
    ChiSqResult = chi2_contingency(CrosstabResult)
    print(col)
    print(ChiSqResult[1])
    CrosstabResult.plot(kind='bar')
    plt.plot()
    print('\n****************\n')

Comorb_Encounter_For_Screening_For_Malignant_Neoplasms
4.704163912301752e-79

****************

Comorb_Encounter_For_Immunization
1.5774452734653173e-75

****************

Comorb_Encntr_For_General_Exam_W_O_Complaint,_Susp_Or_Reprtd_Dx
3.0348991633791696e-64

****************

Comorb_Vitamin_D_Deficiency
7.840048594648414e-24

****************

Comorb_Other_Joint_Disorder_Not_Elsewhere_Classified
3.421072711581398e-42

****************

Comorb_Encntr_For_Oth_Sp_Exam_W_O_Complaint_Suspected_Or_Reprtd_Dx
1.4698346130079742e-35

****************

Comorb_Long_Term_Current_Drug_Therapy
2.725373947984128e-94

****************

Comorb_Dorsalgia
3.657926966497713e-36

****************

Comorb_Personal_History_Of_Other_Diseases_And_Conditions
1.4523357260518627e-37

****************

Comorb_Other_Disorders_Of_Bone_Density_And_Structure
3.8439697713515143e-47

****************

Comorb_Disorders_of_lipoprotein_metabolism_and_other_lipidemias
1.5485241832892978e-21

****************

Comorb_Osteop

All the Comorb variables present significant correlation with the target. Let's check colinearity problems among the variables Comorb.

In [119]:
# Checking problems of colinearity between the comorb variables
p=len(df_comorb.columns)
for i in range(1,len(df_comorb.columns)):
    for j in range(i+1,p):
        CrosstabResult = pd.crosstab(index=df_comorb[df_comorb.columns[i]], columns=df_comorb[df_comorb.columns[j]])
        ChiSqResult = chi2_contingency(CrosstabResult)
        print(df_comorb.columns[i], '-', df_comorb.columns[j])
        print(ChiSqResult[1])

Comorb_Encounter_For_Screening_For_Malignant_Neoplasms - Comorb_Encounter_For_Immunization
2.509940466181988e-40
Comorb_Encounter_For_Screening_For_Malignant_Neoplasms - Comorb_Encntr_For_General_Exam_W_O_Complaint,_Susp_Or_Reprtd_Dx
1.378548355631132e-66
Comorb_Encounter_For_Screening_For_Malignant_Neoplasms - Comorb_Vitamin_D_Deficiency
2.5253696067067724e-05
Comorb_Encounter_For_Screening_For_Malignant_Neoplasms - Comorb_Other_Joint_Disorder_Not_Elsewhere_Classified
1.7841572634361273e-15
Comorb_Encounter_For_Screening_For_Malignant_Neoplasms - Comorb_Encntr_For_Oth_Sp_Exam_W_O_Complaint_Suspected_Or_Reprtd_Dx
5.412594725533224e-60
Comorb_Encounter_For_Screening_For_Malignant_Neoplasms - Comorb_Long_Term_Current_Drug_Therapy
1.5466881239941964e-17
Comorb_Encounter_For_Screening_For_Malignant_Neoplasms - Comorb_Dorsalgia
1.1344956134478818e-15
Comorb_Encounter_For_Screening_For_Malignant_Neoplasms - Comorb_Personal_History_Of_Other_Diseases_And_Conditions
9.776211271020156e-18
Comorb

All these comorb variables present significant correlation, with exception for Comorb_Vitamin_D_Deficiency - Comorb_Other_Disorders_Of_Bone_Density_And_Structure (p-value=0.12) and Comorb_Vitamin_D_Deficiency - Comorb_Personal_history_of_malignant_neoplasm (p-value=0.49). Most of these variable might be removed for the modeling steps, and maybe only one variable will be left. The variable Comorb_Long_Term_Current_Drug_Therapy was the one that presents the highest significant correlation with the target among the Comorb ones. Therefore, this one should be selected. This variable also presented colinearity with all the other commorb variables.

# CONCOM

In [120]:
# Creating a new dataframe to hold all the Concom-related variables
df_concom = df[['Persistency_Flag', 'Concom_Cholesterol_And_Triglyceride_Regulating_Preparations',
       'Concom_Narcotics', 'Concom_Systemic_Corticosteroids_Plain',
       'Concom_Anti_Depressants_And_Mood_Stabilisers',
       'Concom_Fluoroquinolones', 'Concom_Cephalosporins',
       'Concom_Macrolides_And_Similar_Types',
       'Concom_Broad_Spectrum_Penicillins', 'Concom_Anaesthetics_General',
       'Concom_Viral_Vaccines']]

# Visualizing the new concom dataframe
df_concom.head()

Persistency_Flag  \
0       Persistent   
1   Non-Persistent   
2   Non-Persistent   
3   Non-Persistent   
4   Non-Persistent   

  Concom_Cholesterol_And_Triglyceride_Regulating_Preparations  \
0                                                  N            
1                                                  N            
2                                                  Y            
3                                                  N            
4                                                  N            

  Concom_Narcotics Concom_Systemic_Corticosteroids_Plain  \
0                N                                     N   
1                N                                     N   
2                N                                     N   
3                Y                                     Y   
4                Y                                     Y   

  Concom_Anti_Depressants_And_Mood_Stabilisers Concom_Fluoroquinolones  \
0                                            N                       N   
1                                            N                       N   
2                                            N                       N   
3                                            N                       N   
4                                            Y                       N   

  Concom_Cephalosporins Concom_Macrolides_And_Similar_Types  \
0                     N                                   N   
1                     N                                   N   
2                     N                                   N   
3                     N                                   N   
4                     N                                   N   

  Concom_Broad_Spectrum_Penicillins Concom_Anaesthetics_General  \
0                                 N                           N   
1                                 N                           N   
2                                 N                           N   
3                                 N                           N   
4                                 N                           N   

  Concom_Viral_Vaccines  
0                     N  
1                     N  
2                     N  
3                     Y  
4                     N

In [121]:
# Checking correlation between the concom related variables and target
for col in df_concom.columns[1:]:
    CrosstabResult = pd.crosstab(index=df_concom['Persistency_Flag'], columns=df_concom[col])
    ChiSqResult = chi2_contingency(CrosstabResult)
    print(col)
    print(ChiSqResult[1])
    CrosstabResult.plot(kind='bar')
    plt.plot()
    print('\n****************\n')

Concom_Cholesterol_And_Triglyceride_Regulating_Preparations
2.680431689020366e-13

****************

Concom_Narcotics
4.4179993953467654e-29

****************

Concom_Systemic_Corticosteroids_Plain
1.3756487556795202e-45

****************

Concom_Anti_Depressants_And_Mood_Stabilisers
1.5538166175242562e-10

****************

Concom_Fluoroquinolones
2.0037682642622247e-27

****************

Concom_Cephalosporins
3.5950691299126757e-38

****************

Concom_Macrolides_And_Similar_Types
3.461451739236028e-38

****************

Concom_Broad_Spectrum_Penicillins
9.909432107290928e-31

****************

Concom_Anaesthetics_General
2.1339524835408544e-38

****************

Concom_Viral_Vaccines
2.462141024629715e-38

****************



As for the Comorb variables, all the Concom variables also presented significant correlation with the target. Let's check colinearity problems among the variables Concom.

In [122]:
# Checking problems of colinearity between the concom variables
p=len(df_concom.columns)
for i in range(1,len(df_concom.columns)):
    for j in range(i+1,p):
        CrosstabResult = pd.crosstab(index=df_concom[df_concom.columns[i]], columns=df_concom[df_concom.columns[j]])
        ChiSqResult = chi2_contingency(CrosstabResult)
        print(df_concom.columns[i], '-', df_concom.columns[j])
        print(ChiSqResult[1])

Concom_Cholesterol_And_Triglyceride_Regulating_Preparations - Concom_Narcotics
4.3341068445668124e-21
Concom_Cholesterol_And_Triglyceride_Regulating_Preparations - Concom_Systemic_Corticosteroids_Plain
1.3646025878485131e-14
Concom_Cholesterol_And_Triglyceride_Regulating_Preparations - Concom_Anti_Depressants_And_Mood_Stabilisers
3.2659978071508815e-15
Concom_Cholesterol_And_Triglyceride_Regulating_Preparations - Concom_Fluoroquinolones
2.4514500182920217e-25
Concom_Cholesterol_And_Triglyceride_Regulating_Preparations - Concom_Cephalosporins
1.1275550241544843e-10
Concom_Cholesterol_And_Triglyceride_Regulating_Preparations - Concom_Macrolides_And_Similar_Types
4.076290137430696e-14
Concom_Cholesterol_And_Triglyceride_Regulating_Preparations - Concom_Broad_Spectrum_Penicillins
6.602636558127928e-09
Concom_Cholesterol_And_Triglyceride_Regulating_Preparations - Concom_Anaesthetics_General
4.554097888287578e-13
Concom_Cholesterol_And_Triglyceride_Regulating_Preparations - Concom_Viral_Vacc

Feature Selection

KEY OBSERVATIONS FROM EDA:

1) NTM_Speciality variables are correlated with target and to each other.In addition they present almost the same information so it is better to pick 'NTM_Speciality_Bucket' or 'NTM_Speciality_Flag' but not both as they have better data distribution and less categories.

2) Similar to previous case, Dexa variables are also correlated with target and to each other. But 'Dexa_During_Rx' presented a more significant correlation with target and moreover 'Dexa_Freq_During_Rx' is a numerical variable which was tweaked a little to remove outliers because of this there would be a loss of information and since majority of the data is categorical it is better to go with 'Dexa_During_Rx'

3) The variable 'Risk_Segment_Prior_Ntm' doesnt provide significant relation with target variable. So, it will be removed. Between 'Risk_Segment_During_Rx' and 'Change_T_Score' variables as these variables are highly correlated to eachother but 'Risk_Segment_During_Rx' will only be picked as it presents significant correlation with target, less categories and more equally distributed.

4) 'TScore_Bucket_Prior_Ntm' will be removed as well as it did not present any correlation with target variable. 'TScore_Bucket_During_Rx' and 'Change_T_Score' are correlated to eachother.'TScore_Bucket_During_Rx' will be picked as it is significantly correlated and also well distributed than the other variable.

5) Among six variables related to segment and TScore, 2 variables were selected ('Risk_Segment_During_Rx','TScore_Bucket_During_Rx'). One of the possibilites to deal with unknown values would be considering it as 'No change' for these values, but as nearly half of the values are unknown, it may be better to remove these variables too.

6)'Gluco_Record_Prior_Ntm' and 'Gluco_Record_During_Rx' are correlated to each other but 'Gluco_Record_Prior_Ntm' is not correlated with target variable. Therefore, we will keep the 'Gluco_Record_During_Rx' for data modelling.

7) 'Frag_Frac_Prior_Ntm' and 'Frag_Frac_During_Rx' are correlated to each other but 'Frag_Frac_Prior_Ntm' is not correlated to target. So, 'Frag_frac_During_Rx' will not be included for data modelling.

8) 'Adherent_Flag' would be picked for data modelling as it presented a significant correlation with target variable and no correlation with other variables. Among Risk variables, 'Risk_Rheumatoid_Arthritis','Risk_Untreated_Chronic_Hypogonadism','Risk_Smoking_Tobacco', 'Risk_Excessiveness_Thinness', 'Risk_Immobilisation'.

9)All these comorb variables present significant correlation, with exception for Comorb_Vitamin_D_Deficiency - Comorb_Other_Disorders_Of_Bone_Density_And_Structure (p-value=0.12) and Comorb_Vitamin_D_Deficiency - Comorb_Personal_history_of_malignant_neoplasm (p-value=0.49). Most of these variable might be removed for the modeling steps, and maybe only one variable will be left. The variable Comorb_Long_Term_Current_Drug_Therapy was the one that presents the highest significant correlation with the target among the Comorb ones. Therefore, this one should be selected. This variable also presented colinearity with all the other commorb variables.

10) All the Concom variables are correlated to each other, so let's choose the one with more significant correlation with the target. In this case, it should be the Concom_Systemic_Corticosteroids_Plain.


PROBABLE FEATURES ARE AS FOLLOWS:

1)NTM_Speciality_Bucket (or) NTM_Speciality_Flag

2) Dexa_During_Rx 

3) Gluco_Record_During_Rx

4) Frag_Frac_Prior_Ntm

5) Adherent_Flag

6) 'Risk_Rheumatoid_Arthritis'

7) 'Risk_Untreated_chronic_Hypogonadism'

8) 'Risk_Smoking_Tobacco'

9) 'Risk_Excessive_Thinness'

10) 'Risk_Immobalisation'

11) 'Comorb_Long_Term_Current_Drug_Therapy'

12)'Concom_Systemic_Corticosteroids_Plain'

FEATURES TO MAY OR MAYNOT INCLUDE:

1)TScore_Bucket_During_Rx

2)Risk_Segment_During_Rx


Seperating Input features and output labels for model training

In [123]:
EDA_Features=df1[['Ntm_Speciality_Bucket','Dexa_During_Rx','Tscore_Bucket_During_Rx','Risk_Segment_During_Rx','Gluco_Record_During_Rx','Frag_Frac_Prior_Ntm','Adherent_Flag','Risk_Rheumatoid_Arthritis','Risk_Untreated_Chronic_Hypogonadism','Risk_Smoking_Tobacco','Risk_Excessive_Thinness', 'Risk_Immobilization','Comorb_Long_Term_Current_Drug_Therapy','Concom_Systemic_Corticosteroids_Plain']]
Label_Feature=df1['Persistency_Flag']
print(EDA_Features)
print(Label_Feature)
df.columns

      Ntm_Speciality_Bucket  Dexa_During_Rx  Tscore_Bucket_During_Rx  \
0                         1               0                        0   
1                         1               0                        2   
2                         1               0                        0   
3                         1               0                        0   
4                         1               0                        2   
...                     ...             ...                      ...   
3419                      1               0                        2   
3420                      1               0                        2   
3421                      0               1                        0   
3422                      1               0                        2   
3423                      1               0                        2   

      Risk_Segment_During_Rx  Gluco_Record_During_Rx  Frag_Frac_Prior_Ntm  \
0                          2                       0      

Index(['Ptid', 'Persistency_Flag', 'Gender', 'Race', 'Ethnicity', 'Region',
       'Age_Bucket', 'Ntm_Speciality', 'Ntm_Specialist_Flag',
       'Ntm_Speciality_Bucket', 'Gluco_Record_Prior_Ntm',
       'Gluco_Record_During_Rx', 'Dexa_Freq_During_Rx', 'Dexa_During_Rx',
       'Frag_Frac_Prior_Ntm', 'Frag_Frac_During_Rx', 'Risk_Segment_Prior_Ntm',
       'Tscore_Bucket_Prior_Ntm', 'Risk_Segment_During_Rx',
       'Tscore_Bucket_During_Rx', 'Change_T_Score', 'Change_Risk_Segment',
       'Adherent_Flag', 'Idn_Indicator', 'Injectable_Experience_During_Rx',
       'Comorb_Encounter_For_Screening_For_Malignant_Neoplasms',
       'Comorb_Encounter_For_Immunization',
       'Comorb_Encntr_For_General_Exam_W_O_Complaint,_Susp_Or_Reprtd_Dx',
       'Comorb_Vitamin_D_Deficiency',
       'Comorb_Other_Joint_Disorder_Not_Elsewhere_Classified',
       'Comorb_Encntr_For_Oth_Sp_Exam_W_O_Complaint_Suspected_Or_Reprtd_Dx',
       'Comorb_Long_Term_Current_Drug_Therapy', 'Comorb_Dorsalgia',
       'Com

In [124]:
from sklearn.model_selection import cross_val_score
from sklearn.metrics import f1_score
from sklearn.metrics import precision_score
from sklearn.metrics import roc_auc_score,roc_curve
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score,confusion_matrix,ConfusionMatrixDisplay
def metrics_model(X,y_test,predicted_output,model):
    score=accuracy_score(y_test,predicted_output)
    print('The accuracy of the model is :',score)
    f1_Score=f1_score(y_test,predicted_output)
    print("The F1-Score of the model is: ",f1_Score)
    Precision_Score=precision_score(y_test,predicted_output)
    print('The Precision of the model is :',Precision_Score)
    roc_auc=roc_auc_score(y_test,predicted_output)
    print("The ROC-AUC Score for the model is",roc_auc)
    fpr,tpr,thresholds=roc_curve(y_test,predicted_output)
    plt.plot(fpr,tpr)
    plt.xlabel('False Positive Rate')
    plt.ylabel('True Positive Rate')
    plt.show()
    print("the cross validation score is",cross_val_score(model,EDA_Features,Label_Feature,cv=5))
    print("The cross validation F1-score is ",cross_val_score(model,EDA_Features,Label_Feature,cv=5,scoring='f1') )
    confusion_matrix1=confusion_matrix(y_test,predicted_output)
    cm_display=ConfusionMatrixDisplay(confusion_matrix=confusion_matrix1,display_labels=['Non-persistent','Persistent'])
    cm_display.plot()
    plt.show()








EDA Based Feature Selection and Model Training

In [125]:
# Training SVM models using EDA features and hyperparameter tuning following cross validation for better understanding model performance
from sklearn import svm
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import f1_score
from sklearn.metrics import precision_score
from sklearn.metrics import roc_auc_score,roc_curve
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score,confusion_matrix,ConfusionMatrixDisplay
param_grid={'C':[0.1,1,10,15,100],'gamma':[1,0.1,0.01,0.001,0.0001],'kernel':['rbf']}
X_train, X_test, y_train, y_test = train_test_split( EDA_Features, Label_Feature, test_size=0.20)
grid=GridSearchCV(svm.SVC(class_weight={0:0.40,1:0.60}),param_grid,refit=True)
grid.fit(X_train,y_train)
print(grid.best_params_)
print(grid.best_estimator_)
model=svm.SVC(kernel='rbf',class_weight={0:0.40,1:0.60},C=grid.best_params_['C'],gamma=grid.best_params_['gamma'])
model.fit(X_train,y_train)
predicted_output=model.predict(X_test)
f1_Score=f1_score(y_test,predicted_output)
print(f1_Score)
metrics_model(X_test,y_test,predicted_output,model)

# About Model Performances:
# The model seems to be having an accuracy of around 79% and cross_val_score for accuracy is 75%-79%
# But the model seems to be not performing good for persistent class as compared to non-persistent 



{'C': 0.1, 'gamma': 0.1, 'kernel': 'rbf'}
SVC(C=0.1, class_weight={0: 0.4, 1: 0.6}, gamma=0.1)
0.6838709677419356
The accuracy of the model is : 0.7854014598540145
The F1-Score of the model is:  0.6838709677419356
The Precision of the model is : 0.7464788732394366
The ROC-AUC Score for the model is 0.7531205322775761


C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2825291595.py:20: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


the cross validation score is [0.76058394 0.7810219  0.76642336 0.77664234 0.78070175]
The cross validation F1-score is  [0.64957265 0.66517857 0.65517241 0.70520231 0.69262295]


C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2825291595.py:26: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [126]:
# Training Random Forest model using EDA features and hyperparameter tuning following cross validation for better understanding model performance

from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import RandomizedSearchCV
X_train, X_test, y_train, y_test = train_test_split( EDA_Features, Label_Feature, test_size=0.20)
n_estimators = [50,100,120,140,160,180,200]

max_features = ['auto', 'sqrt']
max_depth = [x for x in range(10,101,10)]
min_samples_split = [2,4,6,8,10]
min_samples_leaf = [1, 2, 4,6,8,10]
random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf}
random=RandomizedSearchCV(estimator=RandomForestClassifier(),param_distributions=random_grid,n_iter=100,cv=3,random_state=42,n_jobs=-1)
random.fit(X_train,y_train)
print(random.best_params_)
print(random.best_estimator_)


clf=RandomForestClassifier(n_estimators=random.best_params_['n_estimators'],min_samples_split=random.best_params_['min_samples_leaf'],max_depth=random.best_params_['max_depth'],min_samples_leaf=random.best_params_['min_samples_leaf'],class_weight='balanced')
clf.fit(X_train,y_train)
output=clf.predict(X_test)
score=accuracy_score(y_test,output)
print(score)
metrics_model(X_test,y_test,output,clf)
# About Model Performances:
# The Random forest also has similar accuracy to svm. After considering f1score it seems that random forest seems to be less efficient than SVM





{'n_estimators': 100, 'min_samples_split': 2, 'min_samples_leaf': 6, 'max_features': 'sqrt', 'max_depth': 100}
RandomForestClassifier(max_depth=100, min_samples_leaf=6)
0.7386861313868613
The accuracy of the model is : 0.7386861313868613
The F1-Score of the model is:  0.671559633027523
The Precision of the model is : 0.6443661971830986
The ROC-AUC Score for the model is 0.7314709390587726


C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2825291595.py:20: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


the cross validation score is [0.7620438  0.80145985 0.75474453 0.76058394 0.76023392]
The cross validation F1-score is  [0.68263473 0.73461538 0.66260163 0.70143885 0.69314079]


C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2825291595.py:26: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [127]:
# Training XGBOOST model using EDA features and hyperparameter tuning following cross validation for better understanding model performance

import xgboost as xgb
from sklearn.model_selection import StratifiedKFold
X_train, X_test, y_train, y_test = train_test_split( EDA_Features, Label_Feature, test_size=0.20)
xgb_model=xgb.XGBClassifier(objective='binary:logistic',random_state=42)
xgb_model.fit(X_train,y_train)
param_grid={
    "colsample_bytree":[0.3,0.5,0.8],
    "reg_alpha":[0,0.5,1,5],
    "reg_lambda":[0,0.5,1,5]
}
kfold=StratifiedKFold(n_splits=3,shuffle=True,random_state=0)
grid_search=GridSearchCV(estimator=xgb_model,param_grid=param_grid,cv=kfold,n_jobs=-1)
grid_search.fit(X_train,y_train)
output=grid_search.predict(X_test)
metrics_model(X_test,y_test,output,grid_search)

# About Model Performances:
# The model accuracy seems to be slightly better than the other models but when it comes ti F1-Score it seems to be less than the other two models as model is not able to efficiently identify non-persistent class variables.


The accuracy of the model is : 0.7678832116788321
The F1-Score of the model is:  0.6410835214446953
The Precision of the model is : 0.6995073891625616
The ROC-AUC Score for the model is 0.7272940074906368


C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2825291595.py:20: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


the cross validation score is [0.77372263 0.79562044 0.7649635  0.79124088 0.77923977]
The cross validation F1-score is  [0.6637744  0.70588235 0.64142539 0.71457086 0.68607069]


C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2825291595.py:26: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


Feature Selection through SelectKBest and mutualinfo

In [128]:
# Training SVC from features selected by SelectKbest through mutual_info 
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import chi2,mutual_info_classif
columns=df1.columns.to_list()
dataframe=df1.copy()
dataframe.drop(['Ptid','Persistency_Flag','Dexa_Freq_During_Rx','Count_Of_Risks'],axis=1,inplace=True)
print(columns)
object1 = SelectKBest(mutual_info_classif, k=20).fit(dataframe, Label_Feature)
X_new=object1.transform(dataframe)
print(object1.get_feature_names_out())
X_train, X_test, y_train, y_test = train_test_split( X_new, Label_Feature, test_size=0.10)
model=svm.SVC(kernel='rbf',class_weight='balanced')
model.fit(X_train,y_train)
predicted_output=model.predict(X_test)
metrics_model(X_test,y_test,predicted_output,model)


#About Model Performance
# The model seems to have a bit less accuracy than EDA featuress trained model and also model seems to be having problem in classifying persistent class variables as it has less precision compared to previous trained models.




['Ptid', 'Persistency_Flag', 'Gender', 'Race', 'Ethnicity', 'Region', 'Age_Bucket', 'Ntm_Speciality', 'Ntm_Specialist_Flag', 'Ntm_Speciality_Bucket', 'Gluco_Record_Prior_Ntm', 'Gluco_Record_During_Rx', 'Dexa_During_Rx', 'Frag_Frac_Prior_Ntm', 'Frag_Frac_During_Rx', 'Risk_Segment_Prior_Ntm', 'Tscore_Bucket_Prior_Ntm', 'Risk_Segment_During_Rx', 'Tscore_Bucket_During_Rx', 'Change_T_Score', 'Change_Risk_Segment', 'Adherent_Flag', 'Idn_Indicator', 'Injectable_Experience_During_Rx', 'Comorb_Encounter_For_Screening_For_Malignant_Neoplasms', 'Comorb_Encounter_For_Immunization', 'Comorb_Encntr_For_General_Exam_W_O_Complaint,_Susp_Or_Reprtd_Dx', 'Comorb_Vitamin_D_Deficiency', 'Comorb_Other_Joint_Disorder_Not_Elsewhere_Classified', 'Comorb_Encntr_For_Oth_Sp_Exam_W_O_Complaint_Suspected_Or_Reprtd_Dx', 'Comorb_Long_Term_Current_Drug_Therapy', 'Comorb_Dorsalgia', 'Comorb_Personal_History_Of_Other_Diseases_And_Conditions', 'Comorb_Other_Disorders_Of_Bone_Density_And_Structure', 'Comorb_Disorders_of_l

C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2825291595.py:20: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


the cross validation score is [0.75620438 0.80145985 0.7620438  0.76058394 0.76023392]
The cross validation F1-score is  [0.6719057  0.73745174 0.66391753 0.70397112 0.69172932]


C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2825291595.py:26: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [130]:
# Training RandomForest from features selected by SelectKbest through mutual_info 
from sklearn.feature_selection import SelectKBest
import pickle as pkl
from sklearn.feature_selection import chi2,mutual_info_classif
object1 = SelectKBest(mutual_info_classif, k=20).fit(dataframe, Label_Feature)
X_new=object1.transform(dataframe)
print(object1.get_feature_names_out())
X_train, X_test, y_train, y_test = train_test_split( X_new, Label_Feature, test_size=0.10)
n_estimators = [50,100,120,140,160,180,200]

max_features = ['auto', 'sqrt']
max_depth = [x for x in range(10,101,10)]
min_samples_split = [2,4,6,8,10]
min_samples_leaf = [1, 2, 4,6,8,10]
random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf}
random=RandomizedSearchCV(estimator=RandomForestClassifier(),param_distributions=random_grid,n_iter=100,cv=3,random_state=42,n_jobs=-1)
random.fit(X_train,y_train)
print(random.best_params_)
print(random.best_estimator_)


clf=RandomForestClassifier(n_estimators=random.best_params_['n_estimators'],min_samples_split=random.best_params_['min_samples_leaf'],max_depth=random.best_params_['max_depth'],min_samples_leaf=random.best_params_['min_samples_leaf'],class_weight='balanced')
clf.fit(X_train,y_train)
output=clf.predict(X_test)
score=accuracy_score(y_test,output)
print(score)
metrics_model(X_test,y_test,output,clf)
pkl.dump(clf,open('random_forest_model.pkl','wb'))
# About Model performance
# The model accuracy seems to be better than previous models and also there is a balance between recall and precision leading to a good f1 score.



['Ntm_Speciality' 'Dexa_During_Rx' 'Frag_Frac_During_Rx'
 'Tscore_Bucket_During_Rx'
 'Comorb_Encounter_For_Screening_For_Malignant_Neoplasms'
 'Comorb_Encounter_For_Immunization'
 'Comorb_Encntr_For_General_Exam_W_O_Complaint,_Susp_Or_Reprtd_Dx'
 'Comorb_Other_Joint_Disorder_Not_Elsewhere_Classified'
 'Comorb_Long_Term_Current_Drug_Therapy' 'Comorb_Dorsalgia'
 'Comorb_Personal_History_Of_Other_Diseases_And_Conditions'
 'Comorb_Other_Disorders_Of_Bone_Density_And_Structure'
 'Comorb_Osteoporosis_without_current_pathological_fracture'
 'Comorb_Gastro_esophageal_reflux_disease'
 'Concom_Systemic_Corticosteroids_Plain' 'Concom_Cephalosporins'
 'Concom_Macrolides_And_Similar_Types' 'Concom_Broad_Spectrum_Penicillins'
 'Concom_Anaesthetics_General' 'Concom_Viral_Vaccines']
{'n_estimators': 160, 'min_samples_split': 10, 'min_samples_leaf': 4, 'max_features': 'sqrt', 'max_depth': 80}
RandomForestClassifier(max_depth=80, min_samples_leaf=4, min_samples_split=10,
                       n_estimat

C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2825291595.py:20: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


the cross validation score is [0.76350365 0.79854015 0.75766423 0.7649635  0.75584795]
The cross validation F1-score is  [0.68       0.74319066 0.6653144  0.71119134 0.69927536]


C:\Users\sakal\AppData\Local\Temp\ipykernel_3224\2825291595.py:26: UserWarning: Matplotlib is currently using module://matplotlib_inline.backend_inline, which is a non-GUI backend, so cannot show the figure.
  plt.show()


Dense Neural Network Training

In [ ]:

from tensorflow.keras import Sequential 
from tensorflow.keras.layers import Dense
from tensorflow.keras import metrics
import pickle as pkl
def Dense_Model(X,y,input_shape):
  X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20)
  dense_model=Sequential()
  dense_model.add(Dense(20,activation='relu',input_shape=(input_shape,)))
  dense_model.add(Dense(15,activation='relu'))
  dense_model.add(Dense(10,activation='relu'))
  dense_model.add(Dense(5,activation='relu'))
  dense_model.add(Dense(1,activation='sigmoid'))
  dense_model.compile(optimizer='adam',loss='binary_crossentropy',metrics=['accuracy',metrics.Precision(),metrics.Recall()])
  dense_model.fit(X_train,y_train,validation_split=0.20,epochs=50,batch_size=32)
  loss,acc,precision_score,recall=dense_model.evaluate(X_test,y_test)
  print("the accuracy is",acc)
  print("the precision score is",precision_score)
  print("the recall score is",recall)
  predicted_probability=dense_model.predict([X_test])
  predicted_output=[]
  for x in predicted_probability:
    if x<=0.50:
      predicted_output.append(0)
    if x>0.5:
      predicted_output.append(1)
  print(len(predicted_output))
  print(len(predicted_probability))
  f1Score=(2*(recall*precision_score))/(recall+precision_score)
  print("The F1-score of the Dense Neural Network is ",f1Score)
  pkl.dump(dense_model,open('main_model.pkl','wb'))
 






In [ ]:
!pip install fastapi uvicorn

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.0/57.0 kB 4.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 6.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.0/67.0 kB 6.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 6.4 MB/s eta 0:00:00


In [ ]:
pkl.load(open('main_model.pkl','rb'))

Training Dense Neural Network from EDA features 

In [ ]:
Dense_Model(EDA_Features,Label_Feature,14)
# About Model performance
# The model seems to have good accuracy but the model seems to fail in classifying non-persistent class variables properly and it has less recall compared to other previous models.

Epoch 1/50
69/69 [==============================] - 2s 8ms/step - loss: 0.6807 - accuracy: 0.5970 - precision: 0.3943 - recall: 0.1335 - val_loss: 0.6511 - val_accuracy: 0.6277 - val_precision: 0.0000e+00 - val_recall: 0.0000e+00
Epoch 2/50
69/69 [==============================] - 0s 4ms/step - loss: 0.6154 - accuracy: 0.6458 - precision: 0.8871 - recall: 0.0667 - val_loss: 0.5650 - val_accuracy: 0.7263 - val_precision: 0.8971 - val_recall: 0.2990
Epoch 3/50
69/69 [==============================] - 0s 4ms/step - loss: 0.5372 - accuracy: 0.7581 - precision: 0.7905 - recall: 0.4854 - val_loss: 0.5193 - val_accuracy: 0.7719 - val_precision: 0.7310 - val_recall: 0.6127
Epoch 4/50
69/69 [==============================] - 0s 4ms/step - loss: 0.5063 - accuracy: 0.7745 - precision: 0.7337 - recall: 0.6286 - val_loss: 0.5030 - val_accuracy: 0.7774 - val_precision: 0.7531 - val_recall: 0.5980
Epoch 5/50
69/69 [==============================] - 0s 4ms/step - loss: 0.4991 - accuracy: 0.7777 - prec

Train Dense Network using Features selected from SelectKBest

In [ ]:
#Dense_Model(X_new,Label_Feature,20)
#About Model Performance
# Accuracy of the model seems to same as previous models but it is clear that dense neural networks seems to fail in classifying non-persistent class variable regardless of type of data it was trained using.